# **Data Input and Processing**

In [1]:
from sklearn.datasets import load_files       
from keras.utils import np_utils
import numpy as np
from glob import glob


# define function to load train, test, and validation datasets
def load_dataset(path):
    data = load_files(path)
    files = np.array(data['filenames'])
    targets = np_utils.to_categorical(np.array(data['target']), 2) # not sure if number of classes should be 2
    return files, targets

# load infected cell images and non-infected cell images
images, targets = load_dataset('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/data/cell_images')

# directory test and statistics
names = [item[20:-1] for item in sorted(glob("C:\\Users/user/OneDrive/Documents/capstone/Project_Main/data/cell_images/*/"))]
print('There are %d total categories.' % len(names))
print('There are %s total images.\n' % len(np.hstack([images])))

# Create training, testing and validation dataset
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(images, targets, test_size = 0.2, random_state = 42)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size = 0.25, random_state = 42)

# Pre-process the data into a 4D array for tensorflow (nb_samples, rows, columns, channels)
from keras.preprocessing import image                  
from tqdm import tqdm

def path_to_tensor(img_path):
    # loads RGB image with size 224 x 224 as PIL.Image.Image type
    img = image.load_img(img_path, target_size=(224, 224))
    # convert PIL.Image.Image type to 3D tensor with shape (224, 224, 3) - (rows, columns, channels)
    #     (channels = depth of image which in this case is colour of image)
    x = image.img_to_array(img)
    # convert 3D tensor to 4D tensor with shape (1, 224, 224, 3) and return 4D tensor - (number of images, rows, columns, channels)
    return np.expand_dims(x, axis=0)

def paths_to_tensor(img_paths):
    list_of_tensors = [path_to_tensor(img_path) for img_path in tqdm(img_paths)]
    return np.vstack(list_of_tensors) # stack arrays in a sequence vertically

# #Rescale the images by dividing every pixel in every image by 255
from PIL import ImageFile                            
ImageFile.LOAD_TRUNCATED_IMAGES = True    

# pre-process the data for Keras
X_train = np.delete(X_train, (6587), axis=0) # Indexes may change when next run it
X_train = np.delete(X_train, (6630), axis=0) # Indexes may change when next run it

y_train = np.delete(y_train, (6587), axis=0) # Indexes may change when next run it
y_train = np.delete(y_train, (6630), axis=0) # Indexes may change when next run it

print('There are %d training images.' % len(X_train))
print('There are %d validation images.' % len(X_val))
print('There are %d test images.'% len(X_test))



C:\Users\user\Anaconda3\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


There are 2 total categories.
There are 27560 total images.

There are 16534 training images.
There are 5512 validation images.
There are 5512 test images.


In [2]:
def perf_measure(y_actual, y_hat):
    ''' Function to calculate TP, FP, TN and FN to then calculate sensitivity and specificity ''' 
    
    TP = 0
    FP = 0
    TN = 0
    FN = 0

    for i in range(len(np.array(y_hat))): 
        if np.argmax(y_actual, axis = 1)[i]==np.array(y_hat)[i]==1:
           TP += 1
        if np.array(y_hat)[i]==1 and np.argmax(y_actual, axis = 1)[i]!=np.array(y_hat)[i]:
           FP += 1
        if np.argmax(y_actual, axis = 1)[i]==np.array(y_hat)[i]==0:
           TN += 1
        if np.array(y_hat)[i]==0 and np.argmax(y_actual, axis = 1)[i]!=np.array(y_hat)[i]:
           FN += 1

    return(TP, FP, TN, FN)

# Customised CNN

In [3]:
'''Create Tensor Objects'''

# train_tensors = paths_to_tensor(X_train).astype('float32')/255
# np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/data/objects/train_tensors.npz', tensors = train_tensors) # saved as slow to process
valid_tensors = paths_to_tensor(X_val).astype('float32')/255
test_tensors = paths_to_tensor(X_test).astype('float32')/255
train_tensors = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/data/objects/train_tensors.npz')
train_tensors = train_tensors['tensors']

100%|█████████████████████████████████████████████████████████████████████████████| 5512/5512 [00:31<00:00, 191.58it/s]


In [4]:
# CNN model architecture
from keras.layers import Conv2D, MaxPooling2D, GlobalAveragePooling2D
from keras.layers import Dropout, Flatten, Dense
from keras.models import Sequential

model = Sequential()

model.add(Conv2D(8, (2,2), activation='relu', input_shape=train_tensors.shape[1:]))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Conv2D(16, (2, 2), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Conv2D(64, (2, 2), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Dropout(0.4))
model.add(Flatten())
model.add(Dense(2, activation='softmax'))

model.summary()

Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d_1 (Conv2D)            (None, 223, 223, 8)       104       
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, 111, 111, 8)       0         
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 110, 110, 16)      528       
_________________________________________________________________
max_pooling2d_2 (MaxPooling2 (None, 55, 55, 16)        0         
_________________________________________________________________
conv2d_3 (Conv2D)            (None, 54, 54, 64)        4160      
_________________________________________________________________
max_pooling2d_3 (MaxP

In [5]:
# Compile the model
model.compile(optimizer='rmsprop', loss='categorical_crossentropy', metrics=['accuracy'])

# Train the model
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping  

epochs = 20

checkpointer = ModelCheckpoint(filepath='C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.from_scratch_2.hdf5', 
                               verbose=1, save_best_only=True)

#es = EarlyStopping(monitor='val_loss', mode='min', verbose=1)

model.fit(train_tensors, y_train, 
          validation_data=(valid_tensors, y_val),
          epochs=epochs, batch_size=20, callbacks=[checkpointer], verbose=1)

model.load_weights('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.from_scratch_2.hdf5')

Instructions for updating:
Use tf.cast instead.
Train on 16534 samples, validate on 5512 samples
Epoch 1/20


 4080/16534 [======>.......................] - ETA: 26:39 - loss: 0.7502 - acc: 0.30 - ETA: 22:32 - loss: 2.6131 - acc: 0.37 - ETA: 19:39 - loss: 2.0366 - acc: 0.38 - ETA: 17:43 - loss: 1.7393 - acc: 0.38 - ETA: 16:18 - loss: 1.5478 - acc: 0.40 - ETA: 15:12 - loss: 1.4146 - acc: 0.40 - ETA: 14:17 - loss: 1.3021 - acc: 0.42 - ETA: 13:35 - loss: 1.2365 - acc: 0.43 - ETA: 12:57 - loss: 1.1720 - acc: 0.46 - ETA: 12:25 - loss: 1.1204 - acc: 0.46 - ETA: 11:55 - loss: 1.0781 - acc: 0.47 - ETA: 11:29 - loss: 1.0549 - acc: 0.47 - ETA: 11:05 - loss: 1.0264 - acc: 0.47 - ETA: 10:44 - loss: 1.0046 - acc: 0.47 - ETA: 10:24 - loss: 0.9797 - acc: 0.48 - ETA: 10:07 - loss: 0.9598 - acc: 0.48 - ETA: 9:51 - loss: 0.9404 - acc: 0.4941 - ETA: 9:37 - loss: 0.9395 - acc: 0.491 - ETA: 9:25 - loss: 0.9269 - acc: 0.494 - ETA: 9:13 - loss: 0.9151 - acc: 0.492 - ETA: 9:03 - loss: 0.9031 - acc: 0.495 - ETA: 8:54 - loss: 0.8934 - acc: 0.500 - ETA: 8:45 - loss: 0.8830 - acc: 0.504 - ETA: 8:37 - loss: 0.8752 - acc: 

16440/16534 [============================>.] - ETA: 1:44 - loss: 0.6122 - acc: 0.678 - ETA: 1:44 - loss: 0.6120 - acc: 0.678 - ETA: 1:43 - loss: 0.6118 - acc: 0.678 - ETA: 1:43 - loss: 0.6114 - acc: 0.679 - ETA: 1:42 - loss: 0.6110 - acc: 0.679 - ETA: 1:42 - loss: 0.6106 - acc: 0.679 - ETA: 1:41 - loss: 0.6103 - acc: 0.680 - ETA: 1:41 - loss: 0.6099 - acc: 0.680 - ETA: 1:40 - loss: 0.6094 - acc: 0.680 - ETA: 1:40 - loss: 0.6089 - acc: 0.681 - ETA: 1:39 - loss: 0.6084 - acc: 0.681 - ETA: 1:39 - loss: 0.6080 - acc: 0.681 - ETA: 1:38 - loss: 0.6077 - acc: 0.681 - ETA: 1:38 - loss: 0.6074 - acc: 0.681 - ETA: 1:37 - loss: 0.6071 - acc: 0.682 - ETA: 1:37 - loss: 0.6068 - acc: 0.682 - ETA: 1:36 - loss: 0.6065 - acc: 0.682 - ETA: 1:36 - loss: 0.6065 - acc: 0.682 - ETA: 1:35 - loss: 0.6060 - acc: 0.683 - ETA: 1:35 - loss: 0.6057 - acc: 0.683 - ETA: 1:34 - loss: 0.6052 - acc: 0.684 - ETA: 1:34 - loss: 0.6049 - acc: 0.684 - ETA: 1:33 - loss: 0.6047 - acc: 0.684 - ETA: 1:33 - loss: 0.6042 - acc: 0

16534/16534 [==============================] - ETA: 1s - loss: 0.5550 - acc: 0.728 - ETA: 1s - loss: 0.5556 - acc: 0.728 - ETA: 0s - loss: 0.5552 - acc: 0.728 - ETA: 0s - loss: 0.5559 - acc: 0.728 - 491s 30ms/step - loss: 0.5557 - acc: 0.7286 - val_loss: 0.3339 - val_acc: 0.9087

Epoch 00001: val_loss improved from inf to 0.33389, saving model to C:\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.from_scratch_2.hdf5
Epoch 2/20


 4080/16534 [======>.......................] - ETA: 18:42 - loss: 0.9877 - acc: 0.90 - ETA: 19:58 - loss: 0.5999 - acc: 0.92 - ETA: 19:35 - loss: 0.5285 - acc: 0.90 - ETA: 18:57 - loss: 0.6639 - acc: 0.88 - ETA: 16:48 - loss: 0.5784 - acc: 0.90 - ETA: 15:14 - loss: 0.5265 - acc: 0.90 - ETA: 14:05 - loss: 0.4770 - acc: 0.91 - ETA: 13:08 - loss: 0.4433 - acc: 0.91 - ETA: 12:25 - loss: 0.4091 - acc: 0.92 - ETA: 11:48 - loss: 0.3759 - acc: 0.93 - ETA: 11:18 - loss: 0.3634 - acc: 0.93 - ETA: 10:53 - loss: 0.3699 - acc: 0.91 - ETA: 10:32 - loss: 0.4862 - acc: 0.90 - ETA: 10:15 - loss: 0.4665 - acc: 0.90 - ETA: 10:01 - loss: 0.4625 - acc: 0.91 - ETA: 9:48 - loss: 0.4495 - acc: 0.9125 - ETA: 9:36 - loss: 0.4314 - acc: 0.917 - ETA: 9:25 - loss: 0.4304 - acc: 0.913 - ETA: 9:16 - loss: 0.4206 - acc: 0.915 - ETA: 9:07 - loss: 0.4135 - acc: 0.912 - ETA: 8:59 - loss: 0.4058 - acc: 0.914 - ETA: 8:51 - loss: 0.3941 - acc: 0.918 - ETA: 8:45 - loss: 0.3955 - acc: 0.919 - ETA: 8:38 - loss: 0.3954 - acc: 

...

16420/16534 [============================>.] - ETA: 1:55 - loss: 0.2995 - acc: 0.937 - ETA: 1:54 - loss: 0.2991 - acc: 0.937 - ETA: 1:53 - loss: 0.2993 - acc: 0.937 - ETA: 1:53 - loss: 0.2988 - acc: 0.937 - ETA: 1:52 - loss: 0.2986 - acc: 0.937 - ETA: 1:52 - loss: 0.3002 - acc: 0.937 - ETA: 1:51 - loss: 0.3001 - acc: 0.937 - ETA: 1:51 - loss: 0.3010 - acc: 0.937 - ETA: 1:50 - loss: 0.3010 - acc: 0.937 - ETA: 1:50 - loss: 0.3007 - acc: 0.937 - ETA: 1:49 - loss: 0.3005 - acc: 0.937 - ETA: 1:48 - loss: 0.3003 - acc: 0.937 - ETA: 1:48 - loss: 0.2999 - acc: 0.937 - ETA: 1:47 - loss: 0.2996 - acc: 0.937 - ETA: 1:47 - loss: 0.2995 - acc: 0.937 - ETA: 1:46 - loss: 0.2992 - acc: 0.937 - ETA: 1:46 - loss: 0.2994 - acc: 0.937 - ETA: 1:45 - loss: 0.2991 - acc: 0.937 - ETA: 1:45 - loss: 0.2988 - acc: 0.937 - ETA: 1:44 - loss: 0.2987 - acc: 0.937 - ETA: 1:43 - loss: 0.2990 - acc: 0.936 - ETA: 1:43 - loss: 0.2988 - acc: 0.936 - ETA: 1:42 - loss: 0.2998 - acc: 0.936 - ETA: 1:42 - loss: 0.3007 - acc: 0

16534/16534 [==============================] - ETA: 2s - loss: 0.2999 - acc: 0.937 - ETA: 2s - loss: 0.2996 - acc: 0.937 - ETA: 1s - loss: 0.2995 - acc: 0.937 - ETA: 0s - loss: 0.2993 - acc: 0.937 - ETA: 0s - loss: 0.2993 - acc: 0.937 - 534s 32ms/step - loss: 0.2997 - acc: 0.9376 - val_loss: 0.3137 - val_acc: 0.9369

Epoch 00019: val_loss did not improve from 0.26483
Epoch 20/20


 4080/16534 [======>.......................] - ETA: 6:39 - loss: 0.2792 - acc: 0.850 - ETA: 6:26 - loss: 0.1921 - acc: 0.925 - ETA: 6:21 - loss: 0.1960 - acc: 0.933 - ETA: 6:22 - loss: 0.1952 - acc: 0.937 - ETA: 6:22 - loss: 0.3403 - acc: 0.930 - ETA: 6:29 - loss: 0.3046 - acc: 0.933 - ETA: 6:55 - loss: 0.3816 - acc: 0.928 - ETA: 7:15 - loss: 0.3645 - acc: 0.925 - ETA: 7:08 - loss: 0.3432 - acc: 0.927 - ETA: 7:03 - loss: 0.3953 - acc: 0.930 - ETA: 6:58 - loss: 0.4287 - acc: 0.927 - ETA: 6:55 - loss: 0.3959 - acc: 0.933 - ETA: 6:53 - loss: 0.3896 - acc: 0.926 - ETA: 6:50 - loss: 0.3828 - acc: 0.925 - ETA: 6:48 - loss: 0.3787 - acc: 0.923 - ETA: 6:46 - loss: 0.3602 - acc: 0.928 - ETA: 6:42 - loss: 0.3591 - acc: 0.923 - ETA: 7:21 - loss: 0.3506 - acc: 0.922 - ETA: 7:34 - loss: 0.3413 - acc: 0.923 - ETA: 7:45 - loss: 0.3339 - acc: 0.925 - ETA: 7:56 - loss: 0.3335 - acc: 0.921 - ETA: 8:05 - loss: 0.3271 - acc: 0.920 - ETA: 8:13 - loss: 0.3206 - acc: 0.923 - ETA: 8:20 - loss: 0.3122 - acc: 0

16420/16534 [============================>.] - ETA: 1:55 - loss: 0.2919 - acc: 0.931 - ETA: 1:54 - loss: 0.2919 - acc: 0.931 - ETA: 1:54 - loss: 0.2930 - acc: 0.930 - ETA: 1:53 - loss: 0.2943 - acc: 0.930 - ETA: 1:53 - loss: 0.2941 - acc: 0.930 - ETA: 1:52 - loss: 0.2945 - acc: 0.930 - ETA: 1:52 - loss: 0.2948 - acc: 0.930 - ETA: 1:52 - loss: 0.2946 - acc: 0.930 - ETA: 1:51 - loss: 0.2946 - acc: 0.930 - ETA: 1:51 - loss: 0.2946 - acc: 0.930 - ETA: 1:50 - loss: 0.2945 - acc: 0.930 - ETA: 1:50 - loss: 0.2947 - acc: 0.930 - ETA: 1:49 - loss: 0.2946 - acc: 0.930 - ETA: 1:49 - loss: 0.2944 - acc: 0.930 - ETA: 1:48 - loss: 0.2941 - acc: 0.930 - ETA: 1:48 - loss: 0.2938 - acc: 0.930 - ETA: 1:47 - loss: 0.2938 - acc: 0.930 - ETA: 1:47 - loss: 0.2937 - acc: 0.930 - ETA: 1:46 - loss: 0.2935 - acc: 0.930 - ETA: 1:46 - loss: 0.2932 - acc: 0.930 - ETA: 1:45 - loss: 0.2930 - acc: 0.930 - ETA: 1:45 - loss: 0.2927 - acc: 0.930 - ETA: 1:44 - loss: 0.2924 - acc: 0.930 - ETA: 1:43 - loss: 0.2923 - acc: 0

16534/16534 [==============================] - ETA: 2s - loss: 0.2824 - acc: 0.932 - ETA: 2s - loss: 0.2823 - acc: 0.932 - ETA: 1s - loss: 0.2830 - acc: 0.932 - ETA: 0s - loss: 0.2829 - acc: 0.933 - ETA: 0s - loss: 0.2828 - acc: 0.933 - 543s 33ms/step - loss: 0.2826 - acc: 0.9330 - val_loss: 0.2763 - val_acc: 0.9303

Epoch 00020: val_loss did not improve from 0.26483


In [6]:
# Test the model: Report test accuracy, test sensitivity and test specificity
malaria_predictions = [np.argmax(model.predict(np.expand_dims(tensor, axis=0))) for tensor in test_tensors]

test_accuracy = 100*np.sum(np.array(malaria_predictions)==np.argmax(y_test, axis=1))/len(malaria_predictions)
print('Test accuracy: %.4f%%' % test_accuracy) # getting 91.22% accuracy

TP, FP, TN, FN = perf_measure(y_test, malaria_predictions)

Sensitivity = (TP / (TP + FN))*100
Specificity = (TN / (TN + FP))*100

print('Customised Test Sensitivity: %.4f%%' % Sensitivity)
print('Customised Test Specificity: %.4f%%' % Specificity)

print(TP, TN, FP, FN)

Test accuracy: 92.1807%
Customised Test Sensitivity: 98.0741%
Customised Test Specificity: 86.3043%


### Robustness Check - Adding Gaussian Noise (Customised CNN)

In [3]:
'''Create Tensor Objects'''

# train_tensors = paths_to_tensor(X_train).astype('float32')/255
# np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/data/objects/train_tensors.npz', tensors = train_tensors) # saved as slow to process
valid_tensors = paths_to_tensor(X_val).astype('float32')/255
test_tensors = paths_to_tensor(X_test).astype('float32')/255
train_tensors = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/data/objects/train_tensors.npz')
train_tensors = train_tensors['tensors']

100%|█████████████████████████████████████████████████████████████████████████████| 5512/5512 [00:29<00:00, 187.98it/s]


In [4]:
# CNN model architecture
from keras.layers import Conv2D, MaxPooling2D, GlobalAveragePooling2D
from keras.layers import Dropout, Flatten, Dense
from keras.models import Sequential
from keras.layers import GaussianNoise

model = Sequential()
model.add(GaussianNoise(0.05, input_shape=train_tensors.shape[1:]))
model.add(Conv2D(8, (2,2), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Conv2D(16, (2, 2), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Conv2D(64, (2, 2), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Dropout(0.4))
model.add(Flatten())
model.add(Dense(2, activation='softmax'))

model.summary()

Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
gaussian_noise_1 (GaussianNo (None, 224, 224, 3)       0         
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 223, 223, 8)       104       
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, 111, 111, 8)       0         
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 110, 110, 16)      528       
_________________________________________________________________
max_pooling2d_2 (MaxPooling2 (None, 55, 55, 16)        0         
_________________________________________________________________
conv2d_3 (Conv2D)    

In [5]:
# Compile the model
model.compile(optimizer='rmsprop', loss='categorical_crossentropy', metrics=['accuracy'])

# Train the model
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping  

epochs = 20

checkpointer = ModelCheckpoint(filepath='C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.from_scratch_robustness.hdf5', 
                               verbose=1, save_best_only=True)

#es = EarlyStopping(monitor='val_loss', mode='min', verbose=1)

model.fit(train_tensors, y_train, 
          validation_data=(valid_tensors, y_val),
          epochs=epochs, batch_size=20, callbacks=[checkpointer], verbose=1)

model.load_weights('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.from_scratch_robustness.hdf5')

Instructions for updating:
Use tf.cast instead.
Train on 16534 samples, validate on 5512 samples
Epoch 1/20


 4080/16534 [======>.......................] - ETA: 30:02 - loss: 0.6810 - acc: 0.50 - ETA: 24:14 - loss: 0.8959 - acc: 0.47 - ETA: 20:39 - loss: 1.4598 - acc: 0.51 - ETA: 18:54 - loss: 1.2870 - acc: 0.52 - ETA: 18:02 - loss: 1.1702 - acc: 0.52 - ETA: 17:02 - loss: 1.0984 - acc: 0.51 - ETA: 16:18 - loss: 1.0372 - acc: 0.54 - ETA: 15:29 - loss: 1.0063 - acc: 0.53 - ETA: 14:47 - loss: 0.9714 - acc: 0.53 - ETA: 14:11 - loss: 0.9434 - acc: 0.53 - ETA: 13:36 - loss: 0.9187 - acc: 0.53 - ETA: 13:05 - loss: 0.8965 - acc: 0.54 - ETA: 12:42 - loss: 0.8844 - acc: 0.54 - ETA: 12:18 - loss: 0.8756 - acc: 0.52 - ETA: 11:57 - loss: 0.8747 - acc: 0.52 - ETA: 11:38 - loss: 0.8593 - acc: 0.52 - ETA: 11:20 - loss: 0.8478 - acc: 0.52 - ETA: 11:03 - loss: 0.8370 - acc: 0.53 - ETA: 10:49 - loss: 0.8258 - acc: 0.53 - ETA: 10:36 - loss: 0.8238 - acc: 0.53 - ETA: 10:24 - loss: 0.8193 - acc: 0.53 - ETA: 10:16 - loss: 0.8103 - acc: 0.53 - ETA: 10:09 - loss: 0.7983 - acc: 0.54 - ETA: 10:00 - loss: 0.7964 - acc: 

12240/16534 [=====================>........] - ETA: 3:45 - loss: 0.6693 - acc: 0.605 - ETA: 3:44 - loss: 0.6691 - acc: 0.606 - ETA: 3:44 - loss: 0.6691 - acc: 0.606 - ETA: 3:43 - loss: 0.6688 - acc: 0.606 - ETA: 3:42 - loss: 0.6688 - acc: 0.606 - ETA: 3:42 - loss: 0.6687 - acc: 0.606 - ETA: 3:41 - loss: 0.6685 - acc: 0.606 - ETA: 3:41 - loss: 0.6685 - acc: 0.606 - ETA: 3:40 - loss: 0.6683 - acc: 0.606 - ETA: 3:39 - loss: 0.6682 - acc: 0.606 - ETA: 3:39 - loss: 0.6685 - acc: 0.606 - ETA: 3:38 - loss: 0.6682 - acc: 0.606 - ETA: 3:38 - loss: 0.6683 - acc: 0.606 - ETA: 3:37 - loss: 0.6682 - acc: 0.606 - ETA: 3:37 - loss: 0.6681 - acc: 0.606 - ETA: 3:36 - loss: 0.6679 - acc: 0.607 - ETA: 3:35 - loss: 0.6676 - acc: 0.607 - ETA: 3:35 - loss: 0.6673 - acc: 0.607 - ETA: 3:34 - loss: 0.6688 - acc: 0.607 - ETA: 3:34 - loss: 0.6684 - acc: 0.607 - ETA: 3:33 - loss: 0.6683 - acc: 0.607 - ETA: 3:33 - loss: 0.6683 - acc: 0.607 - ETA: 3:32 - loss: 0.6681 - acc: 0.607 - ETA: 3:31 - loss: 0.6680 - acc: 0

16420/16534 [============================>.] - ETA: 1:54 - loss: 0.6519 - acc: 0.629 - ETA: 1:53 - loss: 0.6518 - acc: 0.629 - ETA: 1:53 - loss: 0.6516 - acc: 0.629 - ETA: 1:52 - loss: 0.6516 - acc: 0.629 - ETA: 1:52 - loss: 0.6514 - acc: 0.629 - ETA: 1:51 - loss: 0.6514 - acc: 0.629 - ETA: 1:51 - loss: 0.6513 - acc: 0.630 - ETA: 1:50 - loss: 0.6511 - acc: 0.630 - ETA: 1:50 - loss: 0.6510 - acc: 0.630 - ETA: 1:49 - loss: 0.6508 - acc: 0.630 - ETA: 1:49 - loss: 0.6506 - acc: 0.630 - ETA: 1:48 - loss: 0.6504 - acc: 0.630 - ETA: 1:48 - loss: 0.6500 - acc: 0.631 - ETA: 1:47 - loss: 0.6504 - acc: 0.631 - ETA: 1:47 - loss: 0.6503 - acc: 0.631 - ETA: 1:46 - loss: 0.6503 - acc: 0.631 - ETA: 1:46 - loss: 0.6501 - acc: 0.631 - ETA: 1:46 - loss: 0.6499 - acc: 0.631 - ETA: 1:45 - loss: 0.6500 - acc: 0.631 - ETA: 1:45 - loss: 0.6498 - acc: 0.631 - ETA: 1:44 - loss: 0.6498 - acc: 0.631 - ETA: 1:44 - loss: 0.6497 - acc: 0.631 - ETA: 1:43 - loss: 0.6496 - acc: 0.631 - ETA: 1:43 - loss: 0.6494 - acc: 0

16534/16534 [==============================] - ETA: 2s - loss: 0.6242 - acc: 0.664 - ETA: 2s - loss: 0.6240 - acc: 0.664 - ETA: 1s - loss: 0.6245 - acc: 0.664 - ETA: 0s - loss: 0.6242 - acc: 0.664 - ETA: 0s - loss: 0.6243 - acc: 0.665 - 553s 33ms/step - loss: 0.6240 - acc: 0.6653 - val_loss: 0.7264 - val_acc: 0.8149

Epoch 00001: val_loss improved from inf to 0.72642, saving model to C:\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.from_scratch_robustness.hdf5
Epoch 2/20


...

16534/16534 [==============================] - ETA: 3s - loss: 0.3157 - acc: 0.932 - ETA: 2s - loss: 0.3154 - acc: 0.932 - ETA: 1s - loss: 0.3152 - acc: 0.932 - ETA: 1s - loss: 0.3152 - acc: 0.932 - ETA: 0s - loss: 0.3149 - acc: 0.932 - 626s 38ms/step - loss: 0.3148 - acc: 0.9324 - val_loss: 0.5031 - val_acc: 0.9372

Epoch 00019: val_loss did not improve from 0.27305
Epoch 20/20


 4080/16534 [======>.......................] - ETA: 9:24 - loss: 1.7175 - acc: 0.850 - ETA: 8:35 - loss: 0.9119 - acc: 0.900 - ETA: 8:34 - loss: 0.6289 - acc: 0.933 - ETA: 8:18 - loss: 0.5033 - acc: 0.937 - ETA: 8:11 - loss: 0.4141 - acc: 0.950 - ETA: 8:14 - loss: 0.3786 - acc: 0.941 - ETA: 8:13 - loss: 0.3340 - acc: 0.950 - ETA: 8:12 - loss: 0.3049 - acc: 0.950 - ETA: 8:11 - loss: 0.3694 - acc: 0.944 - ETA: 8:10 - loss: 0.3334 - acc: 0.950 - ETA: 8:05 - loss: 0.4513 - acc: 0.945 - ETA: 8:00 - loss: 0.5495 - acc: 0.941 - ETA: 7:55 - loss: 0.6322 - acc: 0.938 - ETA: 7:50 - loss: 0.5877 - acc: 0.942 - ETA: 7:46 - loss: 0.5505 - acc: 0.946 - ETA: 7:43 - loss: 0.5814 - acc: 0.943 - ETA: 7:40 - loss: 0.5571 - acc: 0.944 - ETA: 7:37 - loss: 0.5771 - acc: 0.938 - ETA: 7:35 - loss: 0.5574 - acc: 0.939 - ETA: 7:32 - loss: 0.5377 - acc: 0.940 - ETA: 7:30 - loss: 0.5204 - acc: 0.940 - ETA: 7:28 - loss: 0.4995 - acc: 0.943 - ETA: 7:26 - loss: 0.4842 - acc: 0.943 - ETA: 7:24 - loss: 0.4661 - acc: 0

12240/16534 [=====================>........] - ETA: 4:35 - loss: 0.2961 - acc: 0.930 - ETA: 4:34 - loss: 0.2957 - acc: 0.931 - ETA: 4:33 - loss: 0.2950 - acc: 0.931 - ETA: 4:33 - loss: 0.2946 - acc: 0.931 - ETA: 4:32 - loss: 0.2943 - acc: 0.931 - ETA: 4:31 - loss: 0.2947 - acc: 0.931 - ETA: 4:30 - loss: 0.2945 - acc: 0.931 - ETA: 4:29 - loss: 0.2944 - acc: 0.931 - ETA: 4:29 - loss: 0.2941 - acc: 0.931 - ETA: 4:28 - loss: 0.2940 - acc: 0.931 - ETA: 4:27 - loss: 0.2938 - acc: 0.930 - ETA: 4:26 - loss: 0.2935 - acc: 0.931 - ETA: 4:25 - loss: 0.2948 - acc: 0.931 - ETA: 4:25 - loss: 0.2943 - acc: 0.931 - ETA: 4:24 - loss: 0.2955 - acc: 0.931 - ETA: 4:23 - loss: 0.2949 - acc: 0.931 - ETA: 4:22 - loss: 0.2981 - acc: 0.930 - ETA: 4:22 - loss: 0.2989 - acc: 0.930 - ETA: 4:21 - loss: 0.2988 - acc: 0.930 - ETA: 4:20 - loss: 0.2984 - acc: 0.930 - ETA: 4:19 - loss: 0.2998 - acc: 0.930 - ETA: 4:18 - loss: 0.2992 - acc: 0.930 - ETA: 4:18 - loss: 0.2987 - acc: 0.930 - ETA: 4:17 - loss: 0.2981 - acc: 0

16400/16534 [============================>.] - ETA: 2:17 - loss: 0.3003 - acc: 0.930 - ETA: 2:16 - loss: 0.3001 - acc: 0.930 - ETA: 2:16 - loss: 0.3000 - acc: 0.930 - ETA: 2:15 - loss: 0.2996 - acc: 0.930 - ETA: 2:14 - loss: 0.2997 - acc: 0.930 - ETA: 2:14 - loss: 0.2993 - acc: 0.930 - ETA: 2:13 - loss: 0.2990 - acc: 0.930 - ETA: 2:12 - loss: 0.2991 - acc: 0.930 - ETA: 2:11 - loss: 0.2986 - acc: 0.930 - ETA: 2:11 - loss: 0.2985 - acc: 0.930 - ETA: 2:10 - loss: 0.2985 - acc: 0.930 - ETA: 2:09 - loss: 0.2981 - acc: 0.930 - ETA: 2:09 - loss: 0.2990 - acc: 0.930 - ETA: 2:08 - loss: 0.3000 - acc: 0.930 - ETA: 2:07 - loss: 0.2998 - acc: 0.930 - ETA: 2:07 - loss: 0.3001 - acc: 0.930 - ETA: 2:06 - loss: 0.2997 - acc: 0.930 - ETA: 2:05 - loss: 0.3004 - acc: 0.930 - ETA: 2:05 - loss: 0.3000 - acc: 0.930 - ETA: 2:04 - loss: 0.2996 - acc: 0.930 - ETA: 2:03 - loss: 0.2995 - acc: 0.930 - ETA: 2:03 - loss: 0.2993 - acc: 0.930 - ETA: 2:02 - loss: 0.2989 - acc: 0.930 - ETA: 2:01 - loss: 0.2987 - acc: 0

16534/16534 [==============================] - ETA: 3s - loss: 0.2949 - acc: 0.928 - ETA: 3s - loss: 0.2947 - acc: 0.928 - ETA: 2s - loss: 0.2945 - acc: 0.928 - ETA: 1s - loss: 0.2943 - acc: 0.928 - ETA: 1s - loss: 0.2953 - acc: 0.928 - ETA: 0s - loss: 0.2965 - acc: 0.928 - 624s 38ms/step - loss: 0.2964 - acc: 0.9285 - val_loss: 0.2722 - val_acc: 0.9187

Epoch 00020: val_loss improved from 0.27305 to 0.27225, saving model to C:\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.from_scratch_robustness.hdf5


In [8]:
# Test the model: Report test accuracy, test sensitivity and test specificity
malaria_predictions = [np.argmax(model.predict(np.expand_dims(tensor, axis=0))) for tensor in test_tensors]

test_accuracy = 100*np.sum(np.array(malaria_predictions)==np.argmax(y_test, axis=1))/len(malaria_predictions)
print('Test accuracy: %.4f%%' % test_accuracy)

TP, FP, TN, FN = perf_measure(y_test, malaria_predictions)

Sensitivity = (TP / (TP + FN))*100
Specificity = (TN / (TN + FP))*100

print('Customised Test Sensitivity: %.4f%%' % Sensitivity)
print('Customised Test Specificity: %.4f%%' % Specificity)

print(TP, TN, FP, FN)

Test accuracy: 91.3280%
Customised Test Sensitivity: 98.6192%
Customised Test Specificity: 84.0580%
2714 2320 440 38


# Training a ResNet CNN

In [2]:
from keras.applications.resnet50 import ResNet50, preprocess_input
from keras.callbacks import TensorBoard
from time import time
from keras.layers import Conv2D, MaxPooling2D, GlobalAveragePooling2D
from keras.layers import Dropout, Flatten, Dense
from keras.models import Sequential
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping

## Loading the ResNet50 model with pre-trained ImageNet weights
model = ResNet50(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

## Preprocessing the data, so that it can be fed to the pre-trained ResNet50 model.

#resnet_train_input = preprocess_input(train_tensors)
#resnet_valid_input = preprocess_input(valid_tensors)
#resnet_test_input = preprocess_input(test_tensors)

#tensorboard = TensorBoard(log_dir="logs/{}".format(time()))

## Creating bottleneck features for the training data

#train_features_resnet = model.predict(resnet_train_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_train', features=train_features_resnet)

## Creating bottleneck features for the validation data
#valid_features_resnet = model.predict(resnet_valid_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_valid', features=valid_features_resnet)

## Creating bottleneck features for the testing data
#test_features_resnet = model.predict(resnet_test_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_test', features=test_features_resnet)

## Load bottleneck features for training data
train_features_resnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_train.npz')
train_features_resnet = train_features_resnet['features']

## Load bottleneck features for validation data
valid_features_resnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_valid.npz')
valid_features_resnet = valid_features_resnet['features']

## Load bottleneck features for testing data
test_features_resnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_test.npz')
test_features_resnet = test_features_resnet['features']

Instructions for updating:
Colocations handled automatically by placer.


C:\Users\user\Anaconda3\lib\site-packages\keras_applications\resnet50.py:265: UserWarning: The output shape of `ResNet50(include_top=False)` has been changed since Keras 2.2.0.
  warnings.warn('The output shape of `ResNet50(include_top=False)` '


In [3]:
#resnet_model = Sequential()
#resnet_model.add(GlobalAveragePooling2D(input_shape=train_features_resnet.shape[1:]))
#resnet_model.add(Dense(2, activation='sigmoid'))

#resnet_model.summary()

resnet_model = Sequential()

resnet_model.add(Flatten(input_shape=train_features_resnet.shape[1:]))
resnet_model.add(Dense(2, activation='softmax'))

resnet_model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
flatten_1 (Flatten)          (None, 100352)            0         
_________________________________________________________________
dense_1 (Dense)              (None, 2)                 200706    
Total params: 200,706
Trainable params: 200,706
Non-trainable params: 0
_________________________________________________________________


In [4]:
checkpointer_resnet = ModelCheckpoint(filepath='C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.resnet.hdf5', 
                               verbose=1, save_best_only=True)

es = EarlyStopping(monitor='val_loss', mode='min', verbose=1)

resnet_model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

resnet_model.fit(train_features_resnet, y_train, 
          validation_data=(valid_features_resnet, y_val),
          epochs=20, batch_size=20, callbacks=[checkpointer_resnet], verbose=1)

resnet_model.load_weights('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.resnet.hdf5')


Instructions for updating:
Use tf.cast instead.
Train on 16534 samples, validate on 5512 samples
Epoch 1/30
 4080/16534 [======>.......................] - ETA: 41:03 - loss: 0.6977 - acc: 0.50 - ETA: 21:15 - loss: 3.1541 - acc: 0.57 - ETA: 14:34 - loss: 3.3395 - acc: 0.60 - ETA: 11:14 - loss: 2.7179 - acc: 0.57 - ETA: 9:17 - loss: 2.6192 - acc: 0.5300 - ETA: 7:56 - loss: 2.3820 - acc: 0.533 - ETA: 6:58 - loss: 2.2507 - acc: 0.535 - ETA: 6:15 - loss: 2.0490 - acc: 0.537 - ETA: 5:40 - loss: 1.9856 - acc: 0.516 - ETA: 5:13 - loss: 1.8609 - acc: 0.500 - ETA: 4:51 - loss: 1.7700 - acc: 0.518 - ETA: 4:32 - loss: 1.8452 - acc: 0.504 - ETA: 4:16 - loss: 1.7710 - acc: 0.496 - ETA: 4:03 - loss: 1.7227 - acc: 0.500 - ETA: 3:50 - loss: 1.7241 - acc: 0.503 - ETA: 3:40 - loss: 1.6751 - acc: 0.515 - ETA: 3:31 - loss: 1.6238 - acc: 0.517 - ETA: 3:22 - loss: 1.6064 - acc: 0.508 - ETA: 3:16 - loss: 1.5948 - acc: 0.500 - ETA: 3:11 - loss: 1.5436 - acc: 0.510 - ETA: 3:05 - loss: 1.5139 - acc: 0.516 - ETA:

 4080/16534 [======>.......................] - ETA: 1:30 - loss: 0.5750 - acc: 0.650 - ETA: 1:17 - loss: 0.5793 - acc: 0.625 - ETA: 1:17 - loss: 0.6610 - acc: 0.650 - ETA: 1:13 - loss: 0.6461 - acc: 0.675 - ETA: 1:17 - loss: 0.7281 - acc: 0.620 - ETA: 1:16 - loss: 0.7019 - acc: 0.625 - ETA: 1:14 - loss: 0.6958 - acc: 0.628 - ETA: 1:13 - loss: 0.6964 - acc: 0.625 - ETA: 1:13 - loss: 0.7041 - acc: 0.627 - ETA: 1:12 - loss: 0.6896 - acc: 0.630 - ETA: 1:12 - loss: 0.6818 - acc: 0.627 - ETA: 1:13 - loss: 0.6641 - acc: 0.637 - ETA: 1:12 - loss: 0.6646 - acc: 0.634 - ETA: 1:12 - loss: 0.6828 - acc: 0.632 - ETA: 1:11 - loss: 0.6917 - acc: 0.626 - ETA: 1:11 - loss: 0.6719 - acc: 0.640 - ETA: 1:10 - loss: 0.6698 - acc: 0.641 - ETA: 1:10 - loss: 0.6594 - acc: 0.644 - ETA: 1:11 - loss: 0.6579 - acc: 0.644 - ETA: 1:10 - loss: 0.6524 - acc: 0.647 - ETA: 1:10 - loss: 0.6469 - acc: 0.657 - ETA: 1:10 - loss: 0.6397 - acc: 0.661 - ETA: 1:10 - loss: 0.6371 - acc: 0.665 - ETA: 1:10 - loss: 0.6345 - acc: 0

16534/16534 [==============================] - ETA: 21s - loss: 0.7463 - acc: 0.64 - ETA: 21s - loss: 0.7457 - acc: 0.65 - ETA: 21s - loss: 0.7456 - acc: 0.65 - ETA: 20s - loss: 0.7457 - acc: 0.65 - ETA: 20s - loss: 0.7457 - acc: 0.65 - ETA: 20s - loss: 0.7459 - acc: 0.64 - ETA: 20s - loss: 0.7467 - acc: 0.64 - ETA: 20s - loss: 0.7469 - acc: 0.64 - ETA: 20s - loss: 0.7472 - acc: 0.64 - ETA: 20s - loss: 0.7469 - acc: 0.64 - ETA: 20s - loss: 0.7464 - acc: 0.64 - ETA: 19s - loss: 0.7467 - acc: 0.64 - ETA: 19s - loss: 0.7465 - acc: 0.64 - ETA: 19s - loss: 0.7471 - acc: 0.64 - ETA: 19s - loss: 0.7465 - acc: 0.64 - ETA: 19s - loss: 0.7466 - acc: 0.64 - ETA: 19s - loss: 0.7463 - acc: 0.64 - ETA: 19s - loss: 0.7459 - acc: 0.65 - ETA: 19s - loss: 0.7467 - acc: 0.64 - ETA: 19s - loss: 0.7465 - acc: 0.64 - ETA: 18s - loss: 0.7473 - acc: 0.64 - ETA: 18s - loss: 0.7470 - acc: 0.64 - ETA: 18s - loss: 0.7466 - acc: 0.64 - ETA: 18s - loss: 0.7472 - acc: 0.64 - ETA: 18s - loss: 0.7468 - acc: 0.64 - ETA

 4380/16534 [======>.......................] - ETA: 1:17 - loss: 0.5218 - acc: 0.750 - ETA: 1:10 - loss: 0.4185 - acc: 0.800 - ETA: 1:12 - loss: 0.5936 - acc: 0.716 - ETA: 1:13 - loss: 0.5949 - acc: 0.737 - ETA: 1:11 - loss: 0.6154 - acc: 0.720 - ETA: 1:12 - loss: 0.7085 - acc: 0.700 - ETA: 1:11 - loss: 0.7152 - acc: 0.678 - ETA: 1:08 - loss: 0.7173 - acc: 0.675 - ETA: 1:08 - loss: 0.6906 - acc: 0.683 - ETA: 1:06 - loss: 0.6907 - acc: 0.680 - ETA: 1:04 - loss: 0.6959 - acc: 0.681 - ETA: 1:04 - loss: 0.7421 - acc: 0.654 - ETA: 1:03 - loss: 0.7598 - acc: 0.642 - ETA: 1:03 - loss: 0.7678 - acc: 0.642 - ETA: 1:10 - loss: 0.8051 - acc: 0.626 - ETA: 1:20 - loss: 0.8023 - acc: 0.625 - ETA: 1:25 - loss: 0.8271 - acc: 0.620 - ETA: 1:29 - loss: 0.8611 - acc: 0.616 - ETA: 1:31 - loss: 0.8611 - acc: 0.618 - ETA: 1:29 - loss: 0.8731 - acc: 0.615 - ETA: 1:28 - loss: 0.8864 - acc: 0.609 - ETA: 1:26 - loss: 0.8848 - acc: 0.606 - ETA: 1:25 - loss: 0.8675 - acc: 0.613 - ETA: 1:23 - loss: 0.8887 - acc: 0

16534/16534 [==============================] - ETA: 18s - loss: 0.6533 - acc: 0.69 - ETA: 18s - loss: 0.6532 - acc: 0.69 - ETA: 18s - loss: 0.6532 - acc: 0.69 - ETA: 17s - loss: 0.6537 - acc: 0.69 - ETA: 17s - loss: 0.6532 - acc: 0.69 - ETA: 17s - loss: 0.6533 - acc: 0.69 - ETA: 17s - loss: 0.6530 - acc: 0.69 - ETA: 17s - loss: 0.6526 - acc: 0.69 - ETA: 17s - loss: 0.6529 - acc: 0.69 - ETA: 17s - loss: 0.6530 - acc: 0.69 - ETA: 17s - loss: 0.6527 - acc: 0.69 - ETA: 17s - loss: 0.6528 - acc: 0.69 - ETA: 16s - loss: 0.6533 - acc: 0.69 - ETA: 16s - loss: 0.6529 - acc: 0.69 - ETA: 16s - loss: 0.6532 - acc: 0.69 - ETA: 16s - loss: 0.6532 - acc: 0.69 - ETA: 16s - loss: 0.6532 - acc: 0.69 - ETA: 16s - loss: 0.6531 - acc: 0.69 - ETA: 16s - loss: 0.6531 - acc: 0.69 - ETA: 16s - loss: 0.6529 - acc: 0.69 - ETA: 16s - loss: 0.6525 - acc: 0.69 - ETA: 15s - loss: 0.6522 - acc: 0.69 - ETA: 15s - loss: 0.6521 - acc: 0.69 - ETA: 15s - loss: 0.6521 - acc: 0.69 - ETA: 15s - loss: 0.6526 - acc: 0.69 - ETA

...

16534/16534 [==============================] - ETA: 17s - loss: 0.5016 - acc: 0.78 - ETA: 17s - loss: 0.5018 - acc: 0.78 - ETA: 17s - loss: 0.5020 - acc: 0.78 - ETA: 17s - loss: 0.5019 - acc: 0.78 - ETA: 17s - loss: 0.5021 - acc: 0.78 - ETA: 17s - loss: 0.5018 - acc: 0.78 - ETA: 17s - loss: 0.5022 - acc: 0.78 - ETA: 17s - loss: 0.5024 - acc: 0.78 - ETA: 17s - loss: 0.5021 - acc: 0.78 - ETA: 16s - loss: 0.5027 - acc: 0.78 - ETA: 16s - loss: 0.5034 - acc: 0.78 - ETA: 16s - loss: 0.5031 - acc: 0.78 - ETA: 16s - loss: 0.5032 - acc: 0.78 - ETA: 16s - loss: 0.5039 - acc: 0.78 - ETA: 16s - loss: 0.5038 - acc: 0.78 - ETA: 16s - loss: 0.5037 - acc: 0.78 - ETA: 16s - loss: 0.5036 - acc: 0.78 - ETA: 16s - loss: 0.5038 - acc: 0.78 - ETA: 16s - loss: 0.5036 - acc: 0.78 - ETA: 15s - loss: 0.5041 - acc: 0.77 - ETA: 15s - loss: 0.5040 - acc: 0.77 - ETA: 15s - loss: 0.5038 - acc: 0.78 - ETA: 15s - loss: 0.5039 - acc: 0.77 - ETA: 15s - loss: 0.5037 - acc: 0.77 - ETA: 15s - loss: 0.5037 - acc: 0.77 - ETA

 4480/16534 [=======>......................] - ETA: 51s - loss: 0.5615 - acc: 0.70 - ETA: 51s - loss: 0.5048 - acc: 0.75 - ETA: 51s - loss: 0.4814 - acc: 0.76 - ETA: 51s - loss: 0.5778 - acc: 0.72 - ETA: 51s - loss: 0.5451 - acc: 0.73 - ETA: 51s - loss: 0.5900 - acc: 0.71 - ETA: 51s - loss: 0.6286 - acc: 0.71 - ETA: 51s - loss: 0.5851 - acc: 0.73 - ETA: 49s - loss: 0.6011 - acc: 0.72 - ETA: 48s - loss: 0.5441 - acc: 0.75 - ETA: 49s - loss: 0.5229 - acc: 0.75 - ETA: 49s - loss: 0.5188 - acc: 0.75 - ETA: 48s - loss: 0.5008 - acc: 0.76 - ETA: 48s - loss: 0.5572 - acc: 0.75 - ETA: 48s - loss: 0.5448 - acc: 0.75 - ETA: 48s - loss: 0.5611 - acc: 0.75 - ETA: 48s - loss: 0.5486 - acc: 0.75 - ETA: 48s - loss: 0.5606 - acc: 0.75 - ETA: 48s - loss: 0.5656 - acc: 0.74 - ETA: 48s - loss: 0.5638 - acc: 0.74 - ETA: 48s - loss: 0.5527 - acc: 0.75 - ETA: 48s - loss: 0.5478 - acc: 0.75 - ETA: 48s - loss: 0.5493 - acc: 0.75 - ETA: 48s - loss: 0.5404 - acc: 0.76 - ETA: 53s - loss: 0.5358 - acc: 0.76 - ETA

16534/16534 [==============================] - ETA: 17s - loss: 0.4664 - acc: 0.79 - ETA: 17s - loss: 0.4663 - acc: 0.79 - ETA: 17s - loss: 0.4667 - acc: 0.79 - ETA: 17s - loss: 0.4666 - acc: 0.79 - ETA: 17s - loss: 0.4666 - acc: 0.79 - ETA: 17s - loss: 0.4669 - acc: 0.79 - ETA: 17s - loss: 0.4672 - acc: 0.79 - ETA: 17s - loss: 0.4671 - acc: 0.79 - ETA: 16s - loss: 0.4684 - acc: 0.79 - ETA: 16s - loss: 0.4684 - acc: 0.79 - ETA: 16s - loss: 0.4687 - acc: 0.79 - ETA: 16s - loss: 0.4689 - acc: 0.79 - ETA: 16s - loss: 0.4691 - acc: 0.79 - ETA: 16s - loss: 0.4691 - acc: 0.79 - ETA: 16s - loss: 0.4694 - acc: 0.79 - ETA: 16s - loss: 0.4698 - acc: 0.79 - ETA: 16s - loss: 0.4701 - acc: 0.79 - ETA: 15s - loss: 0.4712 - acc: 0.79 - ETA: 15s - loss: 0.4712 - acc: 0.79 - ETA: 15s - loss: 0.4721 - acc: 0.79 - ETA: 15s - loss: 0.4721 - acc: 0.79 - ETA: 15s - loss: 0.4720 - acc: 0.79 - ETA: 15s - loss: 0.4726 - acc: 0.79 - ETA: 15s - loss: 0.4726 - acc: 0.79 - ETA: 15s - loss: 0.4723 - acc: 0.79 - ETA

 4660/16534 [=======>......................] - ETA: 1:04 - loss: 1.2582 - acc: 0.600 - ETA: 47s - loss: 1.0286 - acc: 0.733 - ETA: 48s - loss: 1.0152 - acc: 0.71 - ETA: 48s - loss: 1.0924 - acc: 0.65 - ETA: 49s - loss: 0.9805 - acc: 0.68 - ETA: 49s - loss: 0.9119 - acc: 0.68 - ETA: 49s - loss: 0.8991 - acc: 0.68 - ETA: 49s - loss: 0.9342 - acc: 0.68 - ETA: 49s - loss: 0.9012 - acc: 0.68 - ETA: 49s - loss: 0.8728 - acc: 0.68 - ETA: 49s - loss: 0.8643 - acc: 0.68 - ETA: 49s - loss: 0.8412 - acc: 0.68 - ETA: 48s - loss: 0.8242 - acc: 0.68 - ETA: 48s - loss: 0.8463 - acc: 0.68 - ETA: 48s - loss: 0.8200 - acc: 0.68 - ETA: 48s - loss: 0.8035 - acc: 0.69 - ETA: 48s - loss: 0.8143 - acc: 0.69 - ETA: 48s - loss: 0.7965 - acc: 0.69 - ETA: 47s - loss: 0.8271 - acc: 0.68 - ETA: 48s - loss: 0.8106 - acc: 0.69 - ETA: 48s - loss: 0.7861 - acc: 0.70 - ETA: 48s - loss: 0.7841 - acc: 0.69 - ETA: 48s - loss: 0.7731 - acc: 0.69 - ETA: 48s - loss: 0.7656 - acc: 0.70 - ETA: 48s - loss: 0.7487 - acc: 0.70 - 

16534/16534 [==============================] - ETA: 15s - loss: 0.5414 - acc: 0.77 - ETA: 15s - loss: 0.5412 - acc: 0.77 - ETA: 15s - loss: 0.5409 - acc: 0.77 - ETA: 15s - loss: 0.5405 - acc: 0.77 - ETA: 15s - loss: 0.5404 - acc: 0.77 - ETA: 15s - loss: 0.5402 - acc: 0.77 - ETA: 15s - loss: 0.5400 - acc: 0.77 - ETA: 14s - loss: 0.5397 - acc: 0.77 - ETA: 14s - loss: 0.5393 - acc: 0.77 - ETA: 14s - loss: 0.5390 - acc: 0.77 - ETA: 14s - loss: 0.5387 - acc: 0.77 - ETA: 14s - loss: 0.5384 - acc: 0.77 - ETA: 14s - loss: 0.5387 - acc: 0.77 - ETA: 14s - loss: 0.5383 - acc: 0.77 - ETA: 14s - loss: 0.5380 - acc: 0.77 - ETA: 14s - loss: 0.5384 - acc: 0.77 - ETA: 14s - loss: 0.5380 - acc: 0.77 - ETA: 13s - loss: 0.5383 - acc: 0.77 - ETA: 13s - loss: 0.5384 - acc: 0.77 - ETA: 13s - loss: 0.5382 - acc: 0.77 - ETA: 13s - loss: 0.5382 - acc: 0.77 - ETA: 13s - loss: 0.5385 - acc: 0.77 - ETA: 13s - loss: 0.5380 - acc: 0.77 - ETA: 13s - loss: 0.5375 - acc: 0.77 - ETA: 13s - loss: 0.5375 - acc: 0.77 - ETA

In [6]:
## Test the model: Report test accuracy, test sensitivity and test specificity
resnet_predictions = [np.argmax(resnet_model.predict(np.expand_dims(feature, axis=0))) for feature in test_features_resnet]

test_accuracy = 100*np.sum(np.array(resnet_predictions)==np.argmax(y_test, axis=1))/len(resnet_predictions)
print('Test accuracy: %.4f%%' % test_accuracy)

Resnet_TP, Resnet_FP, Resnet_TN, Resnet_FN = perf_measure(y_test, resnet_predictions)

Resnet_sensitivity = 100*(Resnet_TP / (Resnet_TP + Resnet_FN))
Resnet_specificity = 100*(Resnet_TN / (Resnet_TN + Resnet_FP))

print('Resnet Test Sensitivity: %.4f%%' % Resnet_sensitivity)
print('Resnet Test Specificity: %.4f%%' % Resnet_specificity)

Test accuracy: 76.9775%
Resnet Test Sensitivity: 71.3663%
Resnet Test Specificity: 82.5725%


### Robustness Check - Adding Gaussian Noise (Resnet)

In [3]:
from keras.applications.resnet50 import ResNet50, preprocess_input
from keras.callbacks import TensorBoard
from time import time
from keras.layers import Conv2D, MaxPooling2D, GlobalAveragePooling2D
from keras.layers import Dropout, Flatten, Dense
from keras.models import Sequential
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping

## Loading the ResNet50 model with pre-trained ImageNet weights
model = ResNet50(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

## Preprocessing the data, so that it can be fed to the pre-trained ResNet50 model.

#resnet_train_input = preprocess_input(train_tensors)
#resnet_valid_input = preprocess_input(valid_tensors)
#resnet_test_input = preprocess_input(test_tensors)

#tensorboard = TensorBoard(log_dir="logs/{}".format(time()))

## Creating bottleneck features for the training data

#train_features_resnet = model.predict(resnet_train_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_train', features=train_features_resnet)

## Creating bottleneck features for the validation data
#valid_features_resnet = model.predict(resnet_valid_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_valid', features=valid_features_resnet)

## Creating bottleneck features for the testing data
#test_features_resnet = model.predict(resnet_test_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_test', features=test_features_resnet)

## Load bottleneck features for training data
train_features_resnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_train.npz')
train_features_resnet = train_features_resnet['features']

## Load bottleneck features for validation data
valid_features_resnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_valid.npz')
valid_features_resnet = valid_features_resnet['features']

## Load bottleneck features for testing data
test_features_resnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/resnet_features_test.npz')
test_features_resnet = test_features_resnet['features']

Instructions for updating:
Colocations handled automatically by placer.


C:\Users\user\Anaconda3\lib\site-packages\keras_applications\resnet50.py:265: UserWarning: The output shape of `ResNet50(include_top=False)` has been changed since Keras 2.2.0.
  warnings.warn('The output shape of `ResNet50(include_top=False)` '


In [4]:
#resnet_model = Sequential()
#resnet_model.add(GlobalAveragePooling2D(input_shape=train_features_resnet.shape[1:]))
#resnet_model.add(Dense(2, activation='sigmoid'))

#resnet_model.summary()
from keras.layers import GaussianNoise

resnet_model = Sequential()
resnet_model.add(GaussianNoise(0.05, input_shape=train_features_resnet.shape[1:]))
resnet_model.add(Flatten())
resnet_model.add(Dense(2, activation='softmax'))

resnet_model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
gaussian_noise_1 (GaussianNo (None, 7, 7, 2048)        0         
_________________________________________________________________
flatten_1 (Flatten)          (None, 100352)            0         
_________________________________________________________________
dense_1 (Dense)              (None, 2)                 200706    
Total params: 200,706
Trainable params: 200,706
Non-trainable params: 0
_________________________________________________________________


In [5]:
checkpointer_resnet = ModelCheckpoint(filepath='C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.resnet_robustness.hdf5', 
                               verbose=1, save_best_only=True)

es = EarlyStopping(monitor='val_loss', mode='min', verbose=1)

resnet_model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

resnet_model.fit(train_features_resnet, y_train, 
          validation_data=(valid_features_resnet, y_val),
          epochs=20, batch_size=20, callbacks=[checkpointer_resnet], verbose=1)

resnet_model.load_weights('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.resnet_robustness.hdf5')


Instructions for updating:
Use tf.cast instead.
Train on 16534 samples, validate on 5512 samples
Epoch 1/20


 4080/16534 [======>.......................] - ETA: 53:59 - loss: 0.7179 - acc: 0.50 - ETA: 28:13 - loss: 7.1459 - acc: 0.32 - ETA: 19:55 - loss: 5.5642 - acc: 0.41 - ETA: 15:41 - loss: 4.9246 - acc: 0.43 - ETA: 13:03 - loss: 4.8699 - acc: 0.45 - ETA: 11:16 - loss: 4.6659 - acc: 0.45 - ETA: 10:00 - loss: 4.1700 - acc: 0.46 - ETA: 9:02 - loss: 4.0385 - acc: 0.4500 - ETA: 8:15 - loss: 3.9551 - acc: 0.455 - ETA: 7:40 - loss: 3.7907 - acc: 0.465 - ETA: 7:11 - loss: 3.5620 - acc: 0.454 - ETA: 6:47 - loss: 3.3596 - acc: 0.475 - ETA: 6:26 - loss: 3.3223 - acc: 0.484 - ETA: 6:08 - loss: 3.3096 - acc: 0.492 - ETA: 5:54 - loss: 3.3774 - acc: 0.486 - ETA: 5:40 - loss: 3.2665 - acc: 0.490 - ETA: 5:29 - loss: 3.1157 - acc: 0.497 - ETA: 5:18 - loss: 3.0755 - acc: 0.500 - ETA: 5:09 - loss: 3.1096 - acc: 0.494 - ETA: 5:01 - loss: 3.0524 - acc: 0.500 - ETA: 4:53 - loss: 2.9506 - acc: 0.497 - ETA: 4:45 - loss: 2.8543 - acc: 0.500 - ETA: 4:39 - loss: 2.8430 - acc: 0.495 - ETA: 4:33 - loss: 2.8429 - acc: 

12500/16534 [=====================>........] - ETA: 52s - loss: 0.9921 - acc: 0.57 - ETA: 52s - loss: 0.9914 - acc: 0.57 - ETA: 52s - loss: 0.9905 - acc: 0.57 - ETA: 52s - loss: 0.9895 - acc: 0.57 - ETA: 51s - loss: 0.9892 - acc: 0.57 - ETA: 51s - loss: 0.9889 - acc: 0.57 - ETA: 51s - loss: 0.9887 - acc: 0.57 - ETA: 51s - loss: 0.9882 - acc: 0.57 - ETA: 51s - loss: 0.9874 - acc: 0.57 - ETA: 51s - loss: 0.9868 - acc: 0.57 - ETA: 51s - loss: 0.9855 - acc: 0.57 - ETA: 51s - loss: 0.9848 - acc: 0.57 - ETA: 50s - loss: 0.9837 - acc: 0.57 - ETA: 50s - loss: 0.9832 - acc: 0.58 - ETA: 50s - loss: 0.9821 - acc: 0.58 - ETA: 50s - loss: 0.9819 - acc: 0.58 - ETA: 50s - loss: 0.9818 - acc: 0.58 - ETA: 50s - loss: 0.9811 - acc: 0.57 - ETA: 50s - loss: 0.9807 - acc: 0.58 - ETA: 50s - loss: 0.9792 - acc: 0.58 - ETA: 50s - loss: 0.9790 - acc: 0.58 - ETA: 50s - loss: 0.9789 - acc: 0.58 - ETA: 50s - loss: 0.9785 - acc: 0.58 - ETA: 49s - loss: 0.9775 - acc: 0.58 - ETA: 49s - loss: 0.9768 - acc: 0.58 - ETA

16534/16534 [==============================] - ETA: 28s - loss: 0.9226 - acc: 0.59 - ETA: 27s - loss: 0.9222 - acc: 0.59 - ETA: 27s - loss: 0.9225 - acc: 0.59 - ETA: 27s - loss: 0.9226 - acc: 0.59 - ETA: 27s - loss: 0.9225 - acc: 0.59 - ETA: 27s - loss: 0.9227 - acc: 0.59 - ETA: 27s - loss: 0.9224 - acc: 0.59 - ETA: 27s - loss: 0.9233 - acc: 0.59 - ETA: 26s - loss: 0.9244 - acc: 0.59 - ETA: 26s - loss: 0.9244 - acc: 0.59 - ETA: 26s - loss: 0.9254 - acc: 0.59 - ETA: 26s - loss: 0.9253 - acc: 0.59 - ETA: 26s - loss: 0.9247 - acc: 0.59 - ETA: 26s - loss: 0.9246 - acc: 0.59 - ETA: 26s - loss: 0.9249 - acc: 0.59 - ETA: 25s - loss: 0.9241 - acc: 0.59 - ETA: 25s - loss: 0.9235 - acc: 0.59 - ETA: 25s - loss: 0.9230 - acc: 0.59 - ETA: 25s - loss: 0.9228 - acc: 0.59 - ETA: 25s - loss: 0.9219 - acc: 0.59 - ETA: 25s - loss: 0.9219 - acc: 0.59 - ETA: 25s - loss: 0.9215 - acc: 0.59 - ETA: 25s - loss: 0.9211 - acc: 0.59 - ETA: 25s - loss: 0.9208 - acc: 0.59 - ETA: 24s - loss: 0.9203 - acc: 0.59 - ETA

 4080/16534 [======>.......................] - ETA: 3:12 - loss: 0.7134 - acc: 0.650 - ETA: 2:38 - loss: 0.5299 - acc: 0.750 - ETA: 2:33 - loss: 0.5394 - acc: 0.733 - ETA: 2:28 - loss: 0.5822 - acc: 0.712 - ETA: 2:23 - loss: 0.5503 - acc: 0.740 - ETA: 2:21 - loss: 0.5896 - acc: 0.691 - ETA: 2:20 - loss: 0.5952 - acc: 0.692 - ETA: 2:19 - loss: 0.5897 - acc: 0.693 - ETA: 2:16 - loss: 0.6188 - acc: 0.683 - ETA: 2:14 - loss: 0.6406 - acc: 0.680 - ETA: 2:13 - loss: 0.6575 - acc: 0.668 - ETA: 2:12 - loss: 0.6722 - acc: 0.662 - ETA: 2:13 - loss: 0.6842 - acc: 0.661 - ETA: 2:14 - loss: 0.6749 - acc: 0.667 - ETA: 2:14 - loss: 0.6891 - acc: 0.656 - ETA: 2:14 - loss: 0.6894 - acc: 0.656 - ETA: 2:14 - loss: 0.6907 - acc: 0.652 - ETA: 2:13 - loss: 0.7017 - acc: 0.652 - ETA: 2:12 - loss: 0.7189 - acc: 0.650 - ETA: 2:11 - loss: 0.7014 - acc: 0.660 - ETA: 2:11 - loss: 0.6985 - acc: 0.661 - ETA: 2:09 - loss: 0.6892 - acc: 0.668 - ETA: 2:08 - loss: 0.7093 - acc: 0.663 - ETA: 2:07 - loss: 0.7030 - acc: 0

...

12620/16534 [=====================>........] - ETA: 41s - loss: 0.9403 - acc: 0.70 - ETA: 41s - loss: 0.9401 - acc: 0.70 - ETA: 41s - loss: 0.9397 - acc: 0.70 - ETA: 41s - loss: 0.9385 - acc: 0.70 - ETA: 41s - loss: 0.9392 - acc: 0.70 - ETA: 40s - loss: 0.9392 - acc: 0.70 - ETA: 40s - loss: 0.9414 - acc: 0.70 - ETA: 40s - loss: 0.9420 - acc: 0.70 - ETA: 40s - loss: 0.9419 - acc: 0.70 - ETA: 40s - loss: 0.9432 - acc: 0.70 - ETA: 40s - loss: 0.9464 - acc: 0.70 - ETA: 40s - loss: 0.9451 - acc: 0.70 - ETA: 40s - loss: 0.9441 - acc: 0.70 - ETA: 40s - loss: 0.9462 - acc: 0.70 - ETA: 40s - loss: 0.9514 - acc: 0.70 - ETA: 40s - loss: 0.9513 - acc: 0.70 - ETA: 39s - loss: 0.9531 - acc: 0.70 - ETA: 39s - loss: 0.9569 - acc: 0.70 - ETA: 39s - loss: 0.9595 - acc: 0.70 - ETA: 39s - loss: 0.9589 - acc: 0.70 - ETA: 39s - loss: 0.9586 - acc: 0.70 - ETA: 39s - loss: 0.9572 - acc: 0.70 - ETA: 39s - loss: 0.9562 - acc: 0.70 - ETA: 39s - loss: 0.9551 - acc: 0.70 - ETA: 39s - loss: 0.9543 - acc: 0.70 - ETA

16534/16534 [==============================] - ETA: 19s - loss: 0.9862 - acc: 0.69 - ETA: 19s - loss: 0.9858 - acc: 0.69 - ETA: 19s - loss: 0.9857 - acc: 0.69 - ETA: 19s - loss: 0.9860 - acc: 0.69 - ETA: 19s - loss: 0.9851 - acc: 0.69 - ETA: 18s - loss: 0.9851 - acc: 0.69 - ETA: 18s - loss: 0.9850 - acc: 0.69 - ETA: 18s - loss: 0.9856 - acc: 0.69 - ETA: 18s - loss: 0.9857 - acc: 0.69 - ETA: 18s - loss: 0.9853 - acc: 0.69 - ETA: 18s - loss: 0.9844 - acc: 0.69 - ETA: 18s - loss: 0.9833 - acc: 0.69 - ETA: 18s - loss: 0.9829 - acc: 0.69 - ETA: 18s - loss: 0.9834 - acc: 0.69 - ETA: 18s - loss: 0.9840 - acc: 0.69 - ETA: 17s - loss: 0.9838 - acc: 0.69 - ETA: 17s - loss: 0.9838 - acc: 0.69 - ETA: 17s - loss: 0.9832 - acc: 0.69 - ETA: 17s - loss: 0.9828 - acc: 0.69 - ETA: 17s - loss: 0.9824 - acc: 0.69 - ETA: 17s - loss: 0.9822 - acc: 0.69 - ETA: 17s - loss: 0.9819 - acc: 0.69 - ETA: 17s - loss: 0.9825 - acc: 0.69 - ETA: 17s - loss: 0.9817 - acc: 0.69 - ETA: 17s - loss: 0.9805 - acc: 0.69 - ETA

 4080/16534 [======>.......................] - ETA: 1:48 - loss: 1.1769 - acc: 0.600 - ETA: 1:58 - loss: 0.9202 - acc: 0.675 - ETA: 1:54 - loss: 0.6674 - acc: 0.766 - ETA: 1:54 - loss: 0.6662 - acc: 0.750 - ETA: 1:56 - loss: 0.8049 - acc: 0.720 - ETA: 1:58 - loss: 0.9511 - acc: 0.725 - ETA: 1:57 - loss: 0.8959 - acc: 0.735 - ETA: 1:57 - loss: 0.8856 - acc: 0.743 - ETA: 1:56 - loss: 0.9818 - acc: 0.727 - ETA: 1:56 - loss: 0.9663 - acc: 0.730 - ETA: 1:56 - loss: 0.9213 - acc: 0.736 - ETA: 1:55 - loss: 0.8704 - acc: 0.745 - ETA: 1:55 - loss: 0.8804 - acc: 0.738 - ETA: 1:55 - loss: 0.8899 - acc: 0.728 - ETA: 1:55 - loss: 0.8657 - acc: 0.736 - ETA: 1:54 - loss: 0.8612 - acc: 0.737 - ETA: 1:54 - loss: 0.9057 - acc: 0.732 - ETA: 1:54 - loss: 0.9205 - acc: 0.725 - ETA: 1:54 - loss: 0.8994 - acc: 0.728 - ETA: 1:53 - loss: 0.9220 - acc: 0.722 - ETA: 1:53 - loss: 0.9417 - acc: 0.714 - ETA: 1:53 - loss: 0.9416 - acc: 0.713 - ETA: 1:53 - loss: 0.9417 - acc: 0.706 - ETA: 1:53 - loss: 0.9520 - acc: 0

12560/16534 [=====================>........] - ETA: 46s - loss: 0.9266 - acc: 0.71 - ETA: 46s - loss: 0.9254 - acc: 0.71 - ETA: 46s - loss: 0.9246 - acc: 0.71 - ETA: 46s - loss: 0.9235 - acc: 0.71 - ETA: 46s - loss: 0.9229 - acc: 0.71 - ETA: 46s - loss: 0.9251 - acc: 0.71 - ETA: 45s - loss: 0.9260 - acc: 0.71 - ETA: 45s - loss: 0.9253 - acc: 0.70 - ETA: 45s - loss: 0.9262 - acc: 0.70 - ETA: 45s - loss: 0.9299 - acc: 0.70 - ETA: 45s - loss: 0.9301 - acc: 0.70 - ETA: 45s - loss: 0.9296 - acc: 0.70 - ETA: 45s - loss: 0.9284 - acc: 0.70 - ETA: 44s - loss: 0.9318 - acc: 0.70 - ETA: 44s - loss: 0.9311 - acc: 0.70 - ETA: 44s - loss: 0.9303 - acc: 0.70 - ETA: 44s - loss: 0.9293 - acc: 0.70 - ETA: 44s - loss: 0.9318 - acc: 0.70 - ETA: 44s - loss: 0.9335 - acc: 0.70 - ETA: 44s - loss: 0.9323 - acc: 0.70 - ETA: 44s - loss: 0.9328 - acc: 0.70 - ETA: 44s - loss: 0.9329 - acc: 0.70 - ETA: 44s - loss: 0.9320 - acc: 0.70 - ETA: 44s - loss: 0.9318 - acc: 0.70 - ETA: 43s - loss: 0.9301 - acc: 0.70 - ETA

16534/16534 [==============================] - ETA: 24s - loss: 1.0193 - acc: 0.70 - ETA: 24s - loss: 1.0184 - acc: 0.70 - ETA: 24s - loss: 1.0180 - acc: 0.70 - ETA: 24s - loss: 1.0182 - acc: 0.70 - ETA: 23s - loss: 1.0185 - acc: 0.70 - ETA: 23s - loss: 1.0183 - acc: 0.70 - ETA: 23s - loss: 1.0179 - acc: 0.70 - ETA: 23s - loss: 1.0181 - acc: 0.70 - ETA: 23s - loss: 1.0180 - acc: 0.70 - ETA: 23s - loss: 1.0177 - acc: 0.70 - ETA: 23s - loss: 1.0184 - acc: 0.70 - ETA: 23s - loss: 1.0183 - acc: 0.70 - ETA: 23s - loss: 1.0176 - acc: 0.70 - ETA: 23s - loss: 1.0166 - acc: 0.70 - ETA: 23s - loss: 1.0157 - acc: 0.70 - ETA: 22s - loss: 1.0157 - acc: 0.70 - ETA: 22s - loss: 1.0153 - acc: 0.70 - ETA: 22s - loss: 1.0144 - acc: 0.70 - ETA: 22s - loss: 1.0146 - acc: 0.70 - ETA: 22s - loss: 1.0143 - acc: 0.70 - ETA: 22s - loss: 1.0147 - acc: 0.70 - ETA: 22s - loss: 1.0146 - acc: 0.70 - ETA: 22s - loss: 1.0135 - acc: 0.70 - ETA: 22s - loss: 1.0126 - acc: 0.70 - ETA: 22s - loss: 1.0130 - acc: 0.70 - ETA

In [7]:
## Test the model: Report test accuracy, test sensitivity and test specificity
resnet_predictions = [np.argmax(resnet_model.predict(np.expand_dims(feature, axis=0))) for feature in test_features_resnet]

test_accuracy = 100*np.sum(np.array(resnet_predictions)==np.argmax(y_test, axis=1))/len(resnet_predictions)
print('Test accuracy: %.4f%%' % test_accuracy)

Resnet_TP, Resnet_FP, Resnet_TN, Resnet_FN = perf_measure(y_test, resnet_predictions)

Resnet_sensitivity = 100*(Resnet_TP / (Resnet_TP + Resnet_FN))
Resnet_specificity = 100*(Resnet_TN / (Resnet_TN + Resnet_FP))

print('Resnet Test Sensitivity: %.4f%%' % Resnet_sensitivity)
print('Resnet Test Specificity: %.4f%%' % Resnet_specificity)
print(Resnet_TP, Resnet_TN, Resnet_FP, Resnet_FN)

Test accuracy: 74.4376%
Resnet Test Sensitivity: 75.9811%
Resnet Test Specificity: 72.8986%
2091 2012 748 661


# Training a Inception CNN

In [3]:
from keras.applications.inception_v3 import InceptionV3, preprocess_input
from keras.callbacks import TensorBoard
from time import time
from keras.layers import Conv2D, MaxPooling2D, GlobalAveragePooling2D
from keras.layers import Dropout, Flatten, Dense
from keras.models import Sequential
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping

## Loading the InceptionV3 model with pre-trained ImageNet weights
model = InceptionV3(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

## Preprocessing the data, so that it can be fed to the pre-trained InceptionV3 model. 
#inception_train_input = preprocess_input(train_tensors)

#inception_valid_input = preprocess_input(valid_tensors)

#inception_test_input = preprocess_input(test_tensors)

## Creating bottleneck features for the training data
#train_features_inception = model.predict(inception_train_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_train', features=train_features_inception)

## Creating bottleneck features for the validation data
#valid_features_inception = model.predict(inception_valid_input)resnet_model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_valid', features=valid_features_inception)

## Creating bottleneck features for the testing data
#test_features_inception = model.predict(inception_test_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_test', features=test_features_inception)

## Load bottleneck features for training data
train_features_inception = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_train.npz')
train_features_inception = train_features_inception['features']

## Load bottleneck features for validation data
valid_features_inception = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_valid.npz')
valid_features_inception = valid_features_inception['features']

## Load bottleneck features for testing data
test_features_inception = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_test.npz')
test_features_inception = test_features_inception['features']


inception_model = Sequential()
inception_model.add(Flatten(input_shape=train_features_inception.shape[1:]))
inception_model.add(Dense(2, activation='softmax'))

inception_model.summary()

Instructions for updating:
Colocations handled automatically by placer.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
flatten_1 (Flatten)          (None, 51200)             0         
_________________________________________________________________
dense_1 (Dense)              (None, 2)                 102402    
Total params: 102,402
Trainable params: 102,402
Non-trainable params: 0
_________________________________________________________________


In [4]:
checkpointer_inception = ModelCheckpoint(filepath='C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.inception.hdf5', 
                               verbose=1, save_best_only=True)

inception_model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

inception_model.fit(train_features_inception, y_train, 
          validation_data=(valid_features_inception, y_val),
          epochs=20, batch_size=20, callbacks=[checkpointer_inception], verbose=1)

inception_model.load_weights('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.inception.hdf5')


Instructions for updating:
Use tf.cast instead.
Train on 16534 samples, validate on 5512 samples
Epoch 1/20


 5200/16534 [========>.....................] - ETA: 1:09:39 - loss: 0.9208 - acc: 0.35 - ETA: 23:35 - loss: 3.1613 - acc: 0.4667 - ETA: 17:53 - loss: 2.6631 - acc: 0.47 - ETA: 14:27 - loss: 2.6624 - acc: 0.46 - ETA: 12:10 - loss: 2.6815 - acc: 0.46 - ETA: 10:32 - loss: 2.7607 - acc: 0.43 - ETA: 9:21 - loss: 2.5064 - acc: 0.4688 - ETA: 8:23 - loss: 2.4833 - acc: 0.450 - ETA: 7:39 - loss: 2.4654 - acc: 0.445 - ETA: 7:02 - loss: 2.4357 - acc: 0.445 - ETA: 6:32 - loss: 2.3117 - acc: 0.470 - ETA: 6:07 - loss: 2.1614 - acc: 0.503 - ETA: 5:44 - loss: 2.1161 - acc: 0.503 - ETA: 5:24 - loss: 2.1064 - acc: 0.500 - ETA: 5:07 - loss: 2.0878 - acc: 0.490 - ETA: 4:52 - loss: 2.0231 - acc: 0.502 - ETA: 4:39 - loss: 1.9475 - acc: 0.516 - ETA: 4:28 - loss: 1.9291 - acc: 0.518 - ETA: 4:17 - loss: 1.9211 - acc: 0.517 - ETA: 4:06 - loss: 1.9018 - acc: 0.519 - ETA: 3:58 - loss: 1.8806 - acc: 0.515 - ETA: 3:49 - loss: 1.8324 - acc: 0.519 - ETA: 3:33 - loss: 1.7723 - acc: 0.530 - ETA: 3:27 - loss: 1.7474 - a

 7800/16534 [=============>................] - ETA: 38s - loss: 0.5107 - acc: 0.65 - ETA: 34s - loss: 0.6759 - acc: 0.66 - ETA: 35s - loss: 0.6355 - acc: 0.67 - ETA: 32s - loss: 0.6257 - acc: 0.69 - ETA: 34s - loss: 0.5780 - acc: 0.71 - ETA: 33s - loss: 0.5852 - acc: 0.70 - ETA: 33s - loss: 0.5515 - acc: 0.72 - ETA: 32s - loss: 0.5663 - acc: 0.71 - ETA: 34s - loss: 0.5439 - acc: 0.73 - ETA: 32s - loss: 0.5306 - acc: 0.73 - ETA: 32s - loss: 0.5314 - acc: 0.73 - ETA: 32s - loss: 0.5394 - acc: 0.73 - ETA: 32s - loss: 0.5327 - acc: 0.73 - ETA: 32s - loss: 0.5366 - acc: 0.73 - ETA: 32s - loss: 0.5450 - acc: 0.73 - ETA: 32s - loss: 0.5355 - acc: 0.73 - ETA: 32s - loss: 0.5295 - acc: 0.73 - ETA: 32s - loss: 0.5383 - acc: 0.72 - ETA: 32s - loss: 0.5395 - acc: 0.72 - ETA: 32s - loss: 0.5444 - acc: 0.72 - ETA: 32s - loss: 0.5378 - acc: 0.72 - ETA: 32s - loss: 0.5356 - acc: 0.72 - ETA: 32s - loss: 0.5331 - acc: 0.73 - ETA: 32s - loss: 0.5307 - acc: 0.73 - ETA: 32s - loss: 0.5286 - acc: 0.73 - ETA

11080/16534 [===================>..........] - ETA: 25s - loss: 0.7334 - acc: 0.65 - ETA: 25s - loss: 0.4086 - acc: 0.78 - ETA: 23s - loss: 0.3975 - acc: 0.81 - ETA: 21s - loss: 0.4497 - acc: 0.77 - ETA: 22s - loss: 0.4732 - acc: 0.76 - ETA: 21s - loss: 0.4572 - acc: 0.77 - ETA: 22s - loss: 0.4616 - acc: 0.77 - ETA: 21s - loss: 0.4984 - acc: 0.77 - ETA: 21s - loss: 0.5123 - acc: 0.76 - ETA: 21s - loss: 0.4987 - acc: 0.76 - ETA: 21s - loss: 0.5296 - acc: 0.76 - ETA: 21s - loss: 0.5534 - acc: 0.76 - ETA: 21s - loss: 0.6388 - acc: 0.74 - ETA: 21s - loss: 0.6712 - acc: 0.73 - ETA: 20s - loss: 0.6839 - acc: 0.73 - ETA: 20s - loss: 0.6955 - acc: 0.72 - ETA: 21s - loss: 0.6973 - acc: 0.72 - ETA: 21s - loss: 0.6879 - acc: 0.72 - ETA: 21s - loss: 0.6838 - acc: 0.72 - ETA: 21s - loss: 0.6774 - acc: 0.72 - ETA: 20s - loss: 0.6702 - acc: 0.73 - ETA: 21s - loss: 0.6630 - acc: 0.73 - ETA: 20s - loss: 0.6510 - acc: 0.73 - ETA: 20s - loss: 0.6379 - acc: 0.74 - ETA: 21s - loss: 0.6300 - acc: 0.74 - ETA

12680/16534 [======================>.......] - ETA: 12s - loss: 0.3135 - acc: 0.80 - ETA: 21s - loss: 0.7777 - acc: 0.71 - ETA: 21s - loss: 0.7629 - acc: 0.70 - ETA: 21s - loss: 0.7131 - acc: 0.72 - ETA: 21s - loss: 0.6649 - acc: 0.73 - ETA: 21s - loss: 0.6375 - acc: 0.74 - ETA: 21s - loss: 0.6025 - acc: 0.75 - ETA: 21s - loss: 0.5786 - acc: 0.77 - ETA: 21s - loss: 0.5644 - acc: 0.77 - ETA: 21s - loss: 0.5564 - acc: 0.78 - ETA: 21s - loss: 0.5322 - acc: 0.78 - ETA: 20s - loss: 0.5174 - acc: 0.79 - ETA: 21s - loss: 0.5065 - acc: 0.79 - ETA: 21s - loss: 0.4965 - acc: 0.80 - ETA: 20s - loss: 0.4878 - acc: 0.80 - ETA: 20s - loss: 0.4804 - acc: 0.80 - ETA: 21s - loss: 0.4781 - acc: 0.80 - ETA: 20s - loss: 0.4730 - acc: 0.80 - ETA: 20s - loss: 0.4626 - acc: 0.81 - ETA: 21s - loss: 0.4639 - acc: 0.81 - ETA: 21s - loss: 0.4651 - acc: 0.81 - ETA: 21s - loss: 0.4679 - acc: 0.80 - ETA: 20s - loss: 0.4647 - acc: 0.80 - ETA: 20s - loss: 0.4684 - acc: 0.80 - ETA: 20s - loss: 0.4659 - acc: 0.80 - ETA

16534/16534 [==============================] - ETA: 4s - loss: 0.5282 - acc: 0.772 - ETA: 4s - loss: 0.5301 - acc: 0.771 - ETA: 3s - loss: 0.5318 - acc: 0.770 - ETA: 3s - loss: 0.5321 - acc: 0.770 - ETA: 3s - loss: 0.5313 - acc: 0.770 - ETA: 3s - loss: 0.5306 - acc: 0.770 - ETA: 3s - loss: 0.5299 - acc: 0.771 - ETA: 3s - loss: 0.5302 - acc: 0.770 - ETA: 3s - loss: 0.5291 - acc: 0.771 - ETA: 3s - loss: 0.5285 - acc: 0.771 - ETA: 3s - loss: 0.5278 - acc: 0.771 - ETA: 2s - loss: 0.5276 - acc: 0.771 - ETA: 2s - loss: 0.5276 - acc: 0.771 - ETA: 2s - loss: 0.5280 - acc: 0.771 - ETA: 2s - loss: 0.5284 - acc: 0.771 - ETA: 2s - loss: 0.5277 - acc: 0.771 - ETA: 2s - loss: 0.5284 - acc: 0.771 - ETA: 2s - loss: 0.5281 - acc: 0.771 - ETA: 2s - loss: 0.5280 - acc: 0.770 - ETA: 2s - loss: 0.5271 - acc: 0.771 - ETA: 2s - loss: 0.5264 - acc: 0.771 - ETA: 2s - loss: 0.5256 - acc: 0.772 - ETA: 1s - loss: 0.5265 - acc: 0.771 - ETA: 1s - loss: 0.5276 - acc: 0.771 - ETA: 1s - loss: 0.5285 - acc: 0.771 - ETA

Epoch 00005: val_loss did not improve from 0.57555
Epoch 6/20
16534/16534 [==============================] - ETA: 12s - loss: 0.4679 - acc: 0.75 - ETA: 12s - loss: 0.3326 - acc: 0.84 - ETA: 12s - loss: 0.3190 - acc: 0.84 - ETA: 11s - loss: 0.3687 - acc: 0.82 - ETA: 11s - loss: 0.3602 - acc: 0.83 - ETA: 11s - loss: 0.3457 - acc: 0.83 - ETA: 11s - loss: 0.3513 - acc: 0.83 - ETA: 11s - loss: 0.3595 - acc: 0.83 - ETA: 11s - loss: 0.3515 - acc: 0.83 - ETA: 11s - loss: 0.3661 - acc: 0.82 - ETA: 11s - loss: 0.3661 - acc: 0.83 - ETA: 11s - loss: 0.3732 - acc: 0.82 - ETA: 11s - loss: 0.3734 - acc: 0.83 - ETA: 10s - loss: 0.3824 - acc: 0.82 - ETA: 11s - loss: 0.3829 - acc: 0.82 - ETA: 11s - loss: 0.3849 - acc: 0.82 - ETA: 10s - loss: 0.3752 - acc: 0.82 - ETA: 10s - loss: 0.3705 - acc: 0.83 - ETA: 10s - loss: 0.3740 - acc: 0.83 - ETA: 10s - loss: 0.3793 - acc: 0.82 - ETA: 10s - loss: 0.3970 - acc: 0.81 - ETA: 10s - loss: 0.4014 - acc: 0.82 - ETA: 10s - loss: 0.3950 - acc: 0.82 - ETA: 10s - loss: 

14480/16534 [=========================>....] - ETA: 12s - loss: 0.2968 - acc: 0.90 - ETA: 12s - loss: 0.2930 - acc: 0.89 - ETA: 12s - loss: 0.3914 - acc: 0.82 - ETA: 12s - loss: 0.4244 - acc: 0.80 - ETA: 11s - loss: 0.3999 - acc: 0.81 - ETA: 11s - loss: 0.3939 - acc: 0.81 - ETA: 12s - loss: 0.4017 - acc: 0.80 - ETA: 12s - loss: 0.3905 - acc: 0.81 - ETA: 12s - loss: 0.3701 - acc: 0.82 - ETA: 11s - loss: 0.3743 - acc: 0.82 - ETA: 11s - loss: 0.3822 - acc: 0.81 - ETA: 11s - loss: 0.3847 - acc: 0.81 - ETA: 11s - loss: 0.3748 - acc: 0.82 - ETA: 11s - loss: 0.3713 - acc: 0.82 - ETA: 11s - loss: 0.3743 - acc: 0.82 - ETA: 11s - loss: 0.3752 - acc: 0.82 - ETA: 11s - loss: 0.3772 - acc: 0.82 - ETA: 11s - loss: 0.3781 - acc: 0.82 - ETA: 11s - loss: 0.3741 - acc: 0.82 - ETA: 11s - loss: 0.3844 - acc: 0.82 - ETA: 10s - loss: 0.4008 - acc: 0.81 - ETA: 10s - loss: 0.4107 - acc: 0.81 - ETA: 10s - loss: 0.4245 - acc: 0.81 - ETA: 10s - loss: 0.4243 - acc: 0.81 - ETA: 10s - loss: 0.4183 - acc: 0.81 - ETA

In [10]:
## Test the model: Report test accuracy, test sensitivity and test specificity
inception_predictions = [np.argmax(inception_model.predict(np.expand_dims(feature, axis=0))) for feature in test_features_inception]

test_accuracy = 100*np.sum(np.array(inception_predictions)==np.argmax(y_test, axis=1))/len(inception_predictions)
print('Test accuracy: %.4f%%' % test_accuracy)

inception_TP, inception_FP, inception_TN, inception_FN = perf_measure(y_test, inception_predictions)

inception_sensitivity = (inception_TP / (inception_TP + inception_FN))*100
inception_specificity = (inception_TN / (inception_TN + inception_FP))*100

print('Inception Test Sensitivity: %.4f%%' % inception_sensitivity)
print('Inception Test Specificity: %.4f%%' % inception_specificity)

Test accuracy: 72.3149%
Inception Test Sensitivity: 78.1250%
Inception Test Specificity: 66.5217%


### Robustness - Gaussian Noise (Inception)

In [3]:
from keras.applications.inception_v3 import InceptionV3, preprocess_input
from keras.callbacks import TensorBoard
from time import time
from keras.layers import Conv2D, MaxPooling2D, GlobalAveragePooling2D
from keras.layers import Dropout, Flatten, Dense
from keras.models import Sequential
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping
from keras.layers import GaussianNoise

## Loading the InceptionV3 model with pre-trained ImageNet weights
model = InceptionV3(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

## Preprocessing the data, so that it can be fed to the pre-trained InceptionV3 model. 
#inception_train_input = preprocess_input(train_tensors)

#inception_valid_input = preprocess_input(valid_tensors)

#inception_test_input = preprocess_input(test_tensors)

## Creating bottleneck features for the training data
#train_features_inception = model.predict(inception_train_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_train', features=train_features_inception)

## Creating bottleneck features for the validation data
#valid_features_inception = model.predict(inception_valid_input)resnet_model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_valid', features=valid_features_inception)

## Creating bottleneck features for the testing data
#test_features_inception = model.predict(inception_test_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_test', features=test_features_inception)

## Load bottleneck features for training data
train_features_inception = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_train.npz')
train_features_inception = train_features_inception['features']

## Load bottleneck features for validation data
valid_features_inception = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_valid.npz')
valid_features_inception = valid_features_inception['features']

## Load bottleneck features for testing data
test_features_inception = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/inception_features_test.npz')
test_features_inception = test_features_inception['features']


inception_model = Sequential()
inception_model.add(GaussianNoise(0.05, input_shape=train_features_inception.shape[1:]))
inception_model.add(Flatten())
inception_model.add(Dense(2, activation='softmax'))

inception_model.summary()

Instructions for updating:
Colocations handled automatically by placer.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
gaussian_noise_1 (GaussianNo (None, 5, 5, 2048)        0         
_________________________________________________________________
flatten_1 (Flatten)          (None, 51200)             0         
_________________________________________________________________
dense_1 (Dense)              (None, 2)                 102402    
Total params: 102,402
Trainable params: 102,402
Non-trainable params: 0
_________________________________________________________________


In [4]:
checkpointer_inception = ModelCheckpoint(filepath='C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.inception_robustness.hdf5', 
                               verbose=1, save_best_only=True)

inception_model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

inception_model.fit(train_features_inception, y_train, 
          validation_data=(valid_features_inception, y_val),
          epochs=20, batch_size=20, callbacks=[checkpointer_inception], verbose=1)

inception_model.load_weights('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.inception_robustness.hdf5')


Instructions for updating:
Use tf.cast instead.
Train on 16534 samples, validate on 5512 samples
Epoch 1/20


 4880/16534 [=======>......................] - ETA: 1:32:02 - loss: 0.7980 - acc: 0.40 - ETA: 46:30 - loss: 2.3837 - acc: 0.5000 - ETA: 31:21 - loss: 3.0516 - acc: 0.48 - ETA: 23:47 - loss: 2.4609 - acc: 0.55 - ETA: 19:17 - loss: 2.2575 - acc: 0.56 - ETA: 16:16 - loss: 2.2942 - acc: 0.55 - ETA: 14:05 - loss: 2.1963 - acc: 0.55 - ETA: 12:27 - loss: 2.0011 - acc: 0.57 - ETA: 11:11 - loss: 1.9323 - acc: 0.56 - ETA: 10:12 - loss: 1.8332 - acc: 0.57 - ETA: 9:21 - loss: 1.7636 - acc: 0.5727 - ETA: 8:41 - loss: 1.7055 - acc: 0.583 - ETA: 8:05 - loss: 1.6390 - acc: 0.588 - ETA: 7:36 - loss: 1.6080 - acc: 0.585 - ETA: 7:10 - loss: 1.5952 - acc: 0.586 - ETA: 6:48 - loss: 1.5301 - acc: 0.593 - ETA: 6:28 - loss: 1.5013 - acc: 0.591 - ETA: 6:10 - loss: 1.4690 - acc: 0.597 - ETA: 5:53 - loss: 1.4331 - acc: 0.602 - ETA: 5:39 - loss: 1.4254 - acc: 0.600 - ETA: 5:26 - loss: 1.3988 - acc: 0.607 - ETA: 5:15 - loss: 1.3701 - acc: 0.613 - ETA: 5:04 - loss: 1.3432 - acc: 0.613 - ETA: 4:54 - loss: 1.3634 - a

16534/16534 [==============================] - ETA: 12s - loss: 0.7614 - acc: 0.65 - ETA: 12s - loss: 0.7606 - acc: 0.65 - ETA: 12s - loss: 0.7598 - acc: 0.65 - ETA: 12s - loss: 0.7594 - acc: 0.65 - ETA: 12s - loss: 0.7594 - acc: 0.65 - ETA: 12s - loss: 0.7595 - acc: 0.65 - ETA: 11s - loss: 0.7586 - acc: 0.65 - ETA: 11s - loss: 0.7589 - acc: 0.65 - ETA: 11s - loss: 0.7599 - acc: 0.65 - ETA: 11s - loss: 0.7602 - acc: 0.65 - ETA: 11s - loss: 0.7603 - acc: 0.65 - ETA: 11s - loss: 0.7610 - acc: 0.65 - ETA: 11s - loss: 0.7617 - acc: 0.65 - ETA: 11s - loss: 0.7613 - acc: 0.65 - ETA: 11s - loss: 0.7616 - acc: 0.65 - ETA: 10s - loss: 0.7621 - acc: 0.65 - ETA: 10s - loss: 0.7622 - acc: 0.65 - ETA: 10s - loss: 0.7622 - acc: 0.65 - ETA: 10s - loss: 0.7625 - acc: 0.65 - ETA: 10s - loss: 0.7614 - acc: 0.65 - ETA: 10s - loss: 0.7610 - acc: 0.65 - ETA: 10s - loss: 0.7608 - acc: 0.65 - ETA: 10s - loss: 0.7603 - acc: 0.65 - ETA: 9s - loss: 0.7598 - acc: 0.6574 - ETA: 9s - loss: 0.7598 - acc: 0.657 - ET

 7480/16534 [============>.................] - ETA: 58s - loss: 1.5432 - acc: 0.40 - ETA: 57s - loss: 1.1022 - acc: 0.57 - ETA: 52s - loss: 0.9490 - acc: 0.63 - ETA: 53s - loss: 0.8246 - acc: 0.66 - ETA: 51s - loss: 0.7155 - acc: 0.70 - ETA: 51s - loss: 0.7112 - acc: 0.69 - ETA: 50s - loss: 0.6863 - acc: 0.70 - ETA: 49s - loss: 0.6616 - acc: 0.71 - ETA: 50s - loss: 0.6361 - acc: 0.72 - ETA: 49s - loss: 0.6844 - acc: 0.72 - ETA: 50s - loss: 0.7804 - acc: 0.69 - ETA: 50s - loss: 0.7580 - acc: 0.70 - ETA: 49s - loss: 0.7531 - acc: 0.70 - ETA: 49s - loss: 0.7338 - acc: 0.70 - ETA: 49s - loss: 0.7497 - acc: 0.70 - ETA: 49s - loss: 0.7546 - acc: 0.70 - ETA: 49s - loss: 0.7750 - acc: 0.69 - ETA: 49s - loss: 0.7845 - acc: 0.68 - ETA: 49s - loss: 0.7689 - acc: 0.69 - ETA: 49s - loss: 0.7409 - acc: 0.70 - ETA: 49s - loss: 0.7479 - acc: 0.70 - ETA: 49s - loss: 0.7465 - acc: 0.69 - ETA: 49s - loss: 0.7498 - acc: 0.69 - ETA: 49s - loss: 0.7406 - acc: 0.69 - ETA: 49s - loss: 0.7316 - acc: 0.69 - ETA

16534/16534 [==============================] - ETA: 0s - loss: 0.6480 - acc: 0.716 - ETA: 0s - loss: 0.6488 - acc: 0.716 - ETA: 0s - loss: 0.6492 - acc: 0.716 - ETA: 0s - loss: 0.6503 - acc: 0.716 - ETA: 0s - loss: 0.6494 - acc: 0.717 - ETA: 0s - loss: 0.6495 - acc: 0.716 - ETA: 0s - loss: 0.6500 - acc: 0.716 - ETA: 0s - loss: 0.6508 - acc: 0.716 - ETA: 0s - loss: 0.6516 - acc: 0.716 - ETA: 0s - loss: 0.6515 - acc: 0.716 - ETA: 0s - loss: 0.6562 - acc: 0.716 - ETA: 0s - loss: 0.6561 - acc: 0.716 - ETA: 0s - loss: 0.6587 - acc: 0.715 - 33s 2ms/step - loss: 0.6599 - acc: 0.7154 - val_loss: 0.9724 - val_acc: 0.6720

Epoch 00002: val_loss did not improve from 0.75673
Epoch 3/20


...

16534/16534 [==============================] - ETA: 6s - loss: 0.5469 - acc: 0.806 - ETA: 6s - loss: 0.5475 - acc: 0.806 - ETA: 6s - loss: 0.5468 - acc: 0.806 - ETA: 6s - loss: 0.5467 - acc: 0.806 - ETA: 6s - loss: 0.5464 - acc: 0.806 - ETA: 6s - loss: 0.5462 - acc: 0.806 - ETA: 6s - loss: 0.5461 - acc: 0.806 - ETA: 6s - loss: 0.5460 - acc: 0.806 - ETA: 6s - loss: 0.5457 - acc: 0.806 - ETA: 6s - loss: 0.5467 - acc: 0.805 - ETA: 5s - loss: 0.5460 - acc: 0.806 - ETA: 5s - loss: 0.5461 - acc: 0.806 - ETA: 5s - loss: 0.5452 - acc: 0.806 - ETA: 5s - loss: 0.5448 - acc: 0.806 - ETA: 5s - loss: 0.5450 - acc: 0.806 - ETA: 5s - loss: 0.5453 - acc: 0.806 - ETA: 5s - loss: 0.5448 - acc: 0.806 - ETA: 5s - loss: 0.5443 - acc: 0.806 - ETA: 5s - loss: 0.5442 - acc: 0.806 - ETA: 5s - loss: 0.5451 - acc: 0.806 - ETA: 5s - loss: 0.5455 - acc: 0.806 - ETA: 4s - loss: 0.5459 - acc: 0.805 - ETA: 4s - loss: 0.5461 - acc: 0.805 - ETA: 4s - loss: 0.5456 - acc: 0.805 - ETA: 4s - loss: 0.5462 - acc: 0.805 - ETA

 4560/16534 [=======>......................] - ETA: 57s - loss: 0.4318 - acc: 0.75 - ETA: 54s - loss: 0.3579 - acc: 0.80 - ETA: 56s - loss: 0.3396 - acc: 0.83 - ETA: 55s - loss: 0.4667 - acc: 0.78 - ETA: 57s - loss: 0.4681 - acc: 0.79 - ETA: 57s - loss: 0.4110 - acc: 0.80 - ETA: 58s - loss: 0.3948 - acc: 0.81 - ETA: 58s - loss: 0.3799 - acc: 0.82 - ETA: 58s - loss: 0.4109 - acc: 0.82 - ETA: 57s - loss: 0.3908 - acc: 0.83 - ETA: 58s - loss: 0.4233 - acc: 0.84 - ETA: 58s - loss: 0.4594 - acc: 0.84 - ETA: 58s - loss: 0.4863 - acc: 0.83 - ETA: 58s - loss: 0.4986 - acc: 0.82 - ETA: 58s - loss: 0.5024 - acc: 0.82 - ETA: 58s - loss: 0.5583 - acc: 0.81 - ETA: 58s - loss: 0.5567 - acc: 0.81 - ETA: 58s - loss: 0.5416 - acc: 0.81 - ETA: 58s - loss: 0.5756 - acc: 0.80 - ETA: 58s - loss: 0.5683 - acc: 0.80 - ETA: 59s - loss: 0.5860 - acc: 0.80 - ETA: 58s - loss: 0.5814 - acc: 0.80 - ETA: 58s - loss: 0.5765 - acc: 0.80 - ETA: 58s - loss: 0.5620 - acc: 0.80 - ETA: 58s - loss: 0.5562 - acc: 0.80 - ETA

16534/16534 [==============================] - ETA: 9s - loss: 0.5322 - acc: 0.809 - ETA: 9s - loss: 0.5330 - acc: 0.809 - ETA: 9s - loss: 0.5317 - acc: 0.809 - ETA: 9s - loss: 0.5312 - acc: 0.810 - ETA: 9s - loss: 0.5314 - acc: 0.809 - ETA: 9s - loss: 0.5322 - acc: 0.809 - ETA: 9s - loss: 0.5321 - acc: 0.809 - ETA: 8s - loss: 0.5313 - acc: 0.810 - ETA: 8s - loss: 0.5309 - acc: 0.810 - ETA: 8s - loss: 0.5311 - acc: 0.810 - ETA: 8s - loss: 0.5327 - acc: 0.809 - ETA: 8s - loss: 0.5331 - acc: 0.809 - ETA: 8s - loss: 0.5340 - acc: 0.809 - ETA: 8s - loss: 0.5336 - acc: 0.809 - ETA: 8s - loss: 0.5327 - acc: 0.810 - ETA: 8s - loss: 0.5323 - acc: 0.810 - ETA: 8s - loss: 0.5327 - acc: 0.810 - ETA: 7s - loss: 0.5322 - acc: 0.810 - ETA: 7s - loss: 0.5327 - acc: 0.810 - ETA: 7s - loss: 0.5323 - acc: 0.810 - ETA: 7s - loss: 0.5320 - acc: 0.810 - ETA: 7s - loss: 0.5318 - acc: 0.810 - ETA: 7s - loss: 0.5310 - acc: 0.810 - ETA: 7s - loss: 0.5311 - acc: 0.810 - ETA: 7s - loss: 0.5305 - acc: 0.810 - ETA

 5040/16534 [========>.....................] - ETA: 38s - loss: 0.2360 - acc: 0.85 - ETA: 50s - loss: 0.2796 - acc: 0.87 - ETA: 50s - loss: 0.4453 - acc: 0.81 - ETA: 55s - loss: 0.4457 - acc: 0.83 - ETA: 57s - loss: 0.5184 - acc: 0.80 - ETA: 57s - loss: 0.5280 - acc: 0.79 - ETA: 57s - loss: 0.4937 - acc: 0.80 - ETA: 56s - loss: 0.4597 - acc: 0.81 - ETA: 57s - loss: 0.4528 - acc: 0.81 - ETA: 57s - loss: 0.4185 - acc: 0.82 - ETA: 56s - loss: 0.4060 - acc: 0.83 - ETA: 57s - loss: 0.4322 - acc: 0.82 - ETA: 57s - loss: 0.4624 - acc: 0.81 - ETA: 57s - loss: 0.4544 - acc: 0.81 - ETA: 57s - loss: 0.4435 - acc: 0.82 - ETA: 57s - loss: 0.4479 - acc: 0.82 - ETA: 57s - loss: 0.4439 - acc: 0.81 - ETA: 57s - loss: 0.4295 - acc: 0.82 - ETA: 57s - loss: 0.4235 - acc: 0.82 - ETA: 57s - loss: 0.4130 - acc: 0.82 - ETA: 57s - loss: 0.4006 - acc: 0.82 - ETA: 56s - loss: 0.4128 - acc: 0.82 - ETA: 56s - loss: 0.4309 - acc: 0.81 - ETA: 56s - loss: 0.4214 - acc: 0.82 - ETA: 56s - loss: 0.4212 - acc: 0.82 - ETA

16534/16534 [==============================] - ETA: 8s - loss: 0.5717 - acc: 0.804 - ETA: 8s - loss: 0.5720 - acc: 0.804 - ETA: 7s - loss: 0.5721 - acc: 0.804 - ETA: 7s - loss: 0.5724 - acc: 0.804 - ETA: 7s - loss: 0.5721 - acc: 0.804 - ETA: 7s - loss: 0.5718 - acc: 0.805 - ETA: 7s - loss: 0.5728 - acc: 0.804 - ETA: 7s - loss: 0.5728 - acc: 0.804 - ETA: 7s - loss: 0.5732 - acc: 0.804 - ETA: 7s - loss: 0.5734 - acc: 0.804 - ETA: 7s - loss: 0.5736 - acc: 0.804 - ETA: 7s - loss: 0.5758 - acc: 0.804 - ETA: 6s - loss: 0.5752 - acc: 0.804 - ETA: 6s - loss: 0.5768 - acc: 0.804 - ETA: 6s - loss: 0.5771 - acc: 0.804 - ETA: 6s - loss: 0.5771 - acc: 0.804 - ETA: 6s - loss: 0.5762 - acc: 0.804 - ETA: 6s - loss: 0.5761 - acc: 0.804 - ETA: 6s - loss: 0.5766 - acc: 0.804 - ETA: 6s - loss: 0.5762 - acc: 0.804 - ETA: 6s - loss: 0.5763 - acc: 0.804 - ETA: 6s - loss: 0.5767 - acc: 0.804 - ETA: 5s - loss: 0.5772 - acc: 0.804 - ETA: 5s - loss: 0.5768 - acc: 0.804 - ETA: 5s - loss: 0.5769 - acc: 0.804 - ETA

In [5]:
## Test the model: Report test accuracy, test sensitivity and test specificity
inception_predictions = [np.argmax(inception_model.predict(np.expand_dims(feature, axis=0))) for feature in test_features_inception]

test_accuracy = 100*np.sum(np.array(inception_predictions)==np.argmax(y_test, axis=1))/len(inception_predictions)
print('Test accuracy: %.4f%%' % test_accuracy)

inception_TP, inception_FP, inception_TN, inception_FN = perf_measure(y_test, inception_predictions)

inception_sensitivity = (inception_TP / (inception_TP + inception_FN))*100
inception_specificity = (inception_TN / (inception_TN + inception_FP))*100

print('Inception Test Sensitivity: %.4f%%' % inception_sensitivity)
print('Inception Test Specificity: %.4f%%' % inception_specificity)
print(inception_TP, inception_TN, inception_FP, inception_FN)

Test accuracy: 75.6894%
Inception Test Sensitivity: 76.5262%
Inception Test Specificity: 74.8551%
2106 2066 694 646


# Training a NasNet CNN

In [6]:
from keras.applications.nasnet import NASNetMobile, preprocess_input
from keras.callbacks import TensorBoard
from time import time
from keras.layers import Conv2D, MaxPooling2D, GlobalAveragePooling2D
from keras.layers import Dropout, Flatten, Dense
from keras.models import Sequential
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping

## Loading the NASNetLarge model with pre-trained ImageNet weights
model = NASNetMobile(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

## Preprocessing the data, so that it can be fed to the pre-trained NASNetLarge model. 
#nasnet_train_input = preprocess_input(train_tensors)
#nasnet_valid_input = preprocess_input(valid_tensors)
#nasnet_test_input = preprocess_input(test_tensors)

## Creating bottleneck features for the training data
#train_features_nasnet = model.predict(nasnet_train_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_train', features=train_features_nasnet)

## Creating bottleneck features for the testing data
#valid_features_nasnet = model.predict(nasnet_valid_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_valid', features=valid_features_nasnet)

## Creating bottleneck features for the testing data
#test_features_nasnet = model.predict(nasnet_test_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_test', features=test_features_nasnet)

## Load bottleneck features for training data
train_features_nasnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_train.npz')
train_features_nasnet = train_features_nasnet['features']

## Load bottleneck features for validation data
valid_features_nasnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_valid.npz')
valid_features_nasnet = valid_features_nasnet['features']

## Load bottleneck features for testing data
test_features_nasnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_test.npz')
test_features_nasnet = test_features_nasnet['features']


nasnet_model = Sequential()
nasnet_model.add(Flatten(input_shape=train_features_nasnet.shape[1:]))
nasnet_model.add(Dense(2, activation='softmax'))

nasnet_model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
flatten_2 (Flatten)          (None, 51744)             0         
_________________________________________________________________
dense_2 (Dense)              (None, 2)                 103490    
Total params: 103,490
Trainable params: 103,490
Non-trainable params: 0
_________________________________________________________________


In [7]:
checkpointer_nasnet = ModelCheckpoint(filepath='C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.nasnet.hdf5', 
                               verbose=1, save_best_only=True)

nasnet_model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

nasnet_model.fit(train_features_nasnet, y_train, 
          validation_data=(valid_features_nasnet, y_val),
          epochs=20, batch_size=20, callbacks=[checkpointer_nasnet], verbose=1)

nasnet_model.load_weights('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.nasnet.hdf5')


Train on 16534 samples, validate on 5512 samples
Epoch 1/20
 7000/16534 [===========>..................] - ETA: 4:24:38 - loss: 0.8451 - acc: 0.50 - ETA: 1:28:17 - loss: 4.0667 - acc: 0.53 - ETA: 53:00 - loss: 3.0419 - acc: 0.4900 - ETA: 37:53 - loss: 2.6721 - acc: 0.46 - ETA: 26:30 - loss: 2.3735 - acc: 0.47 - ETA: 20:24 - loss: 2.3890 - acc: 0.49 - ETA: 17:41 - loss: 2.2107 - acc: 0.50 - ETA: 14:44 - loss: 2.1253 - acc: 0.51 - ETA: 13:16 - loss: 2.0594 - acc: 0.50 - ETA: 12:39 - loss: 2.0113 - acc: 0.49 - ETA: 12:06 - loss: 1.9523 - acc: 0.50 - ETA: 11:36 - loss: 1.9458 - acc: 0.49 - ETA: 10:42 - loss: 1.8715 - acc: 0.50 - ETA: 9:55 - loss: 1.8582 - acc: 0.5074 - ETA: 9:35 - loss: 1.8462 - acc: 0.508 - ETA: 8:58 - loss: 1.8018 - acc: 0.505 - ETA: 8:41 - loss: 1.7842 - acc: 0.508 - ETA: 8:26 - loss: 1.7803 - acc: 0.501 - ETA: 7:57 - loss: 1.7521 - acc: 0.498 - ETA: 7:44 - loss: 1.7273 - acc: 0.504 - ETA: 7:32 - loss: 1.7002 - acc: 0.505 - ETA: 7:09 - loss: 1.6614 - acc: 0.496 - ETA: 6

 7060/16534 [===========>..................] - ETA: 51s - loss: 0.7077 - acc: 0.55 - ETA: 38s - loss: 0.6721 - acc: 0.58 - ETA: 35s - loss: 0.6235 - acc: 0.64 - ETA: 34s - loss: 0.6307 - acc: 0.64 - ETA: 34s - loss: 0.6520 - acc: 0.63 - ETA: 33s - loss: 0.6780 - acc: 0.63 - ETA: 33s - loss: 0.6555 - acc: 0.65 - ETA: 33s - loss: 0.6695 - acc: 0.64 - ETA: 33s - loss: 0.7121 - acc: 0.63 - ETA: 34s - loss: 0.7161 - acc: 0.63 - ETA: 34s - loss: 0.7290 - acc: 0.62 - ETA: 33s - loss: 0.7367 - acc: 0.61 - ETA: 33s - loss: 0.7450 - acc: 0.61 - ETA: 33s - loss: 0.7338 - acc: 0.61 - ETA: 34s - loss: 0.7353 - acc: 0.61 - ETA: 34s - loss: 0.7212 - acc: 0.62 - ETA: 33s - loss: 0.7137 - acc: 0.62 - ETA: 33s - loss: 0.7067 - acc: 0.62 - ETA: 33s - loss: 0.6965 - acc: 0.62 - ETA: 33s - loss: 0.7004 - acc: 0.62 - ETA: 33s - loss: 0.6926 - acc: 0.62 - ETA: 33s - loss: 0.6868 - acc: 0.63 - ETA: 33s - loss: 0.6794 - acc: 0.63 - ETA: 33s - loss: 0.6797 - acc: 0.63 - ETA: 33s - loss: 0.6730 - acc: 0.63 - ETA

16534/16534 [==============================] - ETA: 7s - loss: 0.8199 - acc: 0.618 - ETA: 7s - loss: 0.8195 - acc: 0.618 - ETA: 7s - loss: 0.8201 - acc: 0.618 - ETA: 7s - loss: 0.8199 - acc: 0.618 - ETA: 7s - loss: 0.8198 - acc: 0.618 - ETA: 7s - loss: 0.8200 - acc: 0.618 - ETA: 7s - loss: 0.8200 - acc: 0.618 - ETA: 7s - loss: 0.8202 - acc: 0.618 - ETA: 7s - loss: 0.8199 - acc: 0.618 - ETA: 7s - loss: 0.8193 - acc: 0.618 - ETA: 7s - loss: 0.8190 - acc: 0.618 - ETA: 7s - loss: 0.8185 - acc: 0.618 - ETA: 7s - loss: 0.8184 - acc: 0.618 - ETA: 7s - loss: 0.8180 - acc: 0.618 - ETA: 6s - loss: 0.8181 - acc: 0.618 - ETA: 6s - loss: 0.8174 - acc: 0.619 - ETA: 6s - loss: 0.8172 - acc: 0.619 - ETA: 6s - loss: 0.8171 - acc: 0.619 - ETA: 6s - loss: 0.8168 - acc: 0.619 - ETA: 6s - loss: 0.8168 - acc: 0.619 - ETA: 6s - loss: 0.8169 - acc: 0.619 - ETA: 6s - loss: 0.8167 - acc: 0.619 - ETA: 6s - loss: 0.8167 - acc: 0.619 - ETA: 6s - loss: 0.8170 - acc: 0.619 - ETA: 6s - loss: 0.8166 - acc: 0.619 - ETA

 8460/16534 [==============>...............] - ETA: 25s - loss: 0.5756 - acc: 0.70 - ETA: 25s - loss: 0.6222 - acc: 0.68 - ETA: 28s - loss: 0.6994 - acc: 0.64 - ETA: 29s - loss: 0.6598 - acc: 0.67 - ETA: 28s - loss: 0.7104 - acc: 0.64 - ETA: 27s - loss: 0.7525 - acc: 0.61 - ETA: 28s - loss: 0.7333 - acc: 0.61 - ETA: 27s - loss: 0.7746 - acc: 0.60 - ETA: 27s - loss: 0.7622 - acc: 0.61 - ETA: 27s - loss: 0.7552 - acc: 0.60 - ETA: 27s - loss: 0.7415 - acc: 0.60 - ETA: 27s - loss: 0.7333 - acc: 0.60 - ETA: 27s - loss: 0.7246 - acc: 0.62 - ETA: 27s - loss: 0.7173 - acc: 0.62 - ETA: 27s - loss: 0.7267 - acc: 0.62 - ETA: 27s - loss: 0.7249 - acc: 0.62 - ETA: 27s - loss: 0.7179 - acc: 0.62 - ETA: 27s - loss: 0.7066 - acc: 0.63 - ETA: 27s - loss: 0.7015 - acc: 0.63 - ETA: 26s - loss: 0.6970 - acc: 0.63 - ETA: 26s - loss: 0.7012 - acc: 0.63 - ETA: 26s - loss: 0.6972 - acc: 0.63 - ETA: 26s - loss: 0.6971 - acc: 0.63 - ETA: 26s - loss: 0.7032 - acc: 0.62 - ETA: 26s - loss: 0.7056 - acc: 0.62 - ETA

16534/16534 [==============================] - ETA: 13s - loss: 0.7990 - acc: 0.62 - ETA: 13s - loss: 0.7981 - acc: 0.62 - ETA: 13s - loss: 0.7985 - acc: 0.62 - ETA: 13s - loss: 0.7979 - acc: 0.62 - ETA: 13s - loss: 0.7975 - acc: 0.62 - ETA: 13s - loss: 0.7968 - acc: 0.62 - ETA: 13s - loss: 0.7951 - acc: 0.62 - ETA: 13s - loss: 0.7942 - acc: 0.62 - ETA: 13s - loss: 0.7927 - acc: 0.62 - ETA: 13s - loss: 0.7923 - acc: 0.63 - ETA: 13s - loss: 0.7920 - acc: 0.62 - ETA: 13s - loss: 0.7908 - acc: 0.63 - ETA: 12s - loss: 0.7899 - acc: 0.63 - ETA: 12s - loss: 0.7892 - acc: 0.63 - ETA: 12s - loss: 0.7885 - acc: 0.63 - ETA: 12s - loss: 0.7876 - acc: 0.63 - ETA: 12s - loss: 0.7866 - acc: 0.63 - ETA: 12s - loss: 0.7857 - acc: 0.63 - ETA: 12s - loss: 0.7854 - acc: 0.63 - ETA: 12s - loss: 0.7843 - acc: 0.63 - ETA: 12s - loss: 0.7831 - acc: 0.63 - ETA: 12s - loss: 0.7833 - acc: 0.63 - ETA: 12s - loss: 0.7827 - acc: 0.63 - ETA: 12s - loss: 0.7825 - acc: 0.63 - ETA: 12s - loss: 0.7819 - acc: 0.63 - ETA

...

 8560/16534 [==============>...............] - ETA: 25s - loss: 0.4810 - acc: 0.75 - ETA: 25s - loss: 0.7087 - acc: 0.61 - ETA: 25s - loss: 0.7853 - acc: 0.61 - ETA: 25s - loss: 0.8098 - acc: 0.61 - ETA: 25s - loss: 0.7079 - acc: 0.66 - ETA: 25s - loss: 0.6646 - acc: 0.68 - ETA: 25s - loss: 0.6654 - acc: 0.69 - ETA: 25s - loss: 0.6280 - acc: 0.72 - ETA: 25s - loss: 0.6099 - acc: 0.72 - ETA: 25s - loss: 0.5903 - acc: 0.73 - ETA: 25s - loss: 0.5790 - acc: 0.74 - ETA: 25s - loss: 0.5679 - acc: 0.74 - ETA: 25s - loss: 0.5573 - acc: 0.74 - ETA: 25s - loss: 0.5625 - acc: 0.74 - ETA: 25s - loss: 0.5940 - acc: 0.73 - ETA: 25s - loss: 0.6107 - acc: 0.72 - ETA: 25s - loss: 0.6023 - acc: 0.72 - ETA: 25s - loss: 0.6073 - acc: 0.72 - ETA: 25s - loss: 0.6134 - acc: 0.72 - ETA: 24s - loss: 0.6054 - acc: 0.73 - ETA: 24s - loss: 0.6106 - acc: 0.73 - ETA: 24s - loss: 0.6159 - acc: 0.72 - ETA: 24s - loss: 0.6086 - acc: 0.72 - ETA: 24s - loss: 0.6101 - acc: 0.72 - ETA: 24s - loss: 0.6080 - acc: 0.72 - ETA

 8560/16534 [==============>...............] - ETA: 25s - loss: 0.4210 - acc: 0.80 - ETA: 25s - loss: 0.7456 - acc: 0.61 - ETA: 25s - loss: 0.7221 - acc: 0.64 - ETA: 25s - loss: 0.7498 - acc: 0.66 - ETA: 25s - loss: 0.7638 - acc: 0.63 - ETA: 25s - loss: 0.7438 - acc: 0.63 - ETA: 25s - loss: 0.7399 - acc: 0.64 - ETA: 26s - loss: 0.7360 - acc: 0.65 - ETA: 26s - loss: 0.7630 - acc: 0.63 - ETA: 25s - loss: 0.7524 - acc: 0.64 - ETA: 26s - loss: 0.7157 - acc: 0.65 - ETA: 26s - loss: 0.6741 - acc: 0.68 - ETA: 26s - loss: 0.6694 - acc: 0.69 - ETA: 25s - loss: 0.6638 - acc: 0.69 - ETA: 25s - loss: 0.6615 - acc: 0.69 - ETA: 25s - loss: 0.6602 - acc: 0.69 - ETA: 25s - loss: 0.6514 - acc: 0.69 - ETA: 25s - loss: 0.6506 - acc: 0.69 - ETA: 25s - loss: 0.6620 - acc: 0.68 - ETA: 25s - loss: 0.6745 - acc: 0.68 - ETA: 25s - loss: 0.6659 - acc: 0.69 - ETA: 25s - loss: 0.6596 - acc: 0.69 - ETA: 25s - loss: 0.6597 - acc: 0.69 - ETA: 25s - loss: 0.6594 - acc: 0.69 - ETA: 25s - loss: 0.6607 - acc: 0.68 - ETA

16534/16534 [==============================] - ETA: 13s - loss: 0.5963 - acc: 0.72 - ETA: 13s - loss: 0.5957 - acc: 0.72 - ETA: 13s - loss: 0.5946 - acc: 0.72 - ETA: 12s - loss: 0.5952 - acc: 0.72 - ETA: 12s - loss: 0.5945 - acc: 0.72 - ETA: 12s - loss: 0.5943 - acc: 0.72 - ETA: 12s - loss: 0.5950 - acc: 0.72 - ETA: 12s - loss: 0.5943 - acc: 0.72 - ETA: 12s - loss: 0.5968 - acc: 0.72 - ETA: 12s - loss: 0.5973 - acc: 0.72 - ETA: 12s - loss: 0.5980 - acc: 0.71 - ETA: 12s - loss: 0.5970 - acc: 0.72 - ETA: 12s - loss: 0.5955 - acc: 0.72 - ETA: 12s - loss: 0.5943 - acc: 0.72 - ETA: 12s - loss: 0.5934 - acc: 0.72 - ETA: 12s - loss: 0.5936 - acc: 0.72 - ETA: 12s - loss: 0.5932 - acc: 0.72 - ETA: 12s - loss: 0.5925 - acc: 0.72 - ETA: 11s - loss: 0.5918 - acc: 0.72 - ETA: 11s - loss: 0.5915 - acc: 0.72 - ETA: 11s - loss: 0.5912 - acc: 0.72 - ETA: 11s - loss: 0.5913 - acc: 0.72 - ETA: 11s - loss: 0.5916 - acc: 0.72 - ETA: 11s - loss: 0.5911 - acc: 0.72 - ETA: 11s - loss: 0.5916 - acc: 0.72 - ETA

 8560/16534 [==============>...............] - ETA: 25s - loss: 1.6875 - acc: 0.40 - ETA: 25s - loss: 1.0550 - acc: 0.53 - ETA: 25s - loss: 1.0005 - acc: 0.56 - ETA: 25s - loss: 1.0306 - acc: 0.56 - ETA: 25s - loss: 0.9417 - acc: 0.57 - ETA: 25s - loss: 0.9209 - acc: 0.57 - ETA: 25s - loss: 0.9114 - acc: 0.57 - ETA: 25s - loss: 0.8713 - acc: 0.59 - ETA: 26s - loss: 0.8387 - acc: 0.61 - ETA: 25s - loss: 0.8113 - acc: 0.63 - ETA: 25s - loss: 0.7922 - acc: 0.63 - ETA: 25s - loss: 0.7705 - acc: 0.64 - ETA: 25s - loss: 0.7542 - acc: 0.64 - ETA: 25s - loss: 0.7356 - acc: 0.65 - ETA: 25s - loss: 0.7236 - acc: 0.66 - ETA: 25s - loss: 0.7074 - acc: 0.66 - ETA: 25s - loss: 0.6835 - acc: 0.67 - ETA: 25s - loss: 0.6682 - acc: 0.68 - ETA: 25s - loss: 0.6539 - acc: 0.69 - ETA: 25s - loss: 0.6450 - acc: 0.69 - ETA: 25s - loss: 0.6511 - acc: 0.69 - ETA: 25s - loss: 0.6503 - acc: 0.69 - ETA: 25s - loss: 0.6563 - acc: 0.69 - ETA: 25s - loss: 0.6779 - acc: 0.68 - ETA: 25s - loss: 0.6855 - acc: 0.68 - ETA

16534/16534 [==============================] - ETA: 12s - loss: 0.6460 - acc: 0.71 - ETA: 12s - loss: 0.6457 - acc: 0.71 - ETA: 12s - loss: 0.6447 - acc: 0.71 - ETA: 12s - loss: 0.6436 - acc: 0.71 - ETA: 12s - loss: 0.6431 - acc: 0.71 - ETA: 12s - loss: 0.6424 - acc: 0.71 - ETA: 12s - loss: 0.6421 - acc: 0.71 - ETA: 12s - loss: 0.6431 - acc: 0.71 - ETA: 12s - loss: 0.6437 - acc: 0.71 - ETA: 12s - loss: 0.6431 - acc: 0.71 - ETA: 12s - loss: 0.6428 - acc: 0.71 - ETA: 12s - loss: 0.6424 - acc: 0.71 - ETA: 12s - loss: 0.6425 - acc: 0.71 - ETA: 12s - loss: 0.6446 - acc: 0.71 - ETA: 11s - loss: 0.6460 - acc: 0.71 - ETA: 11s - loss: 0.6458 - acc: 0.71 - ETA: 11s - loss: 0.6447 - acc: 0.71 - ETA: 11s - loss: 0.6437 - acc: 0.71 - ETA: 11s - loss: 0.6430 - acc: 0.71 - ETA: 11s - loss: 0.6421 - acc: 0.71 - ETA: 11s - loss: 0.6421 - acc: 0.71 - ETA: 11s - loss: 0.6425 - acc: 0.71 - ETA: 11s - loss: 0.6429 - acc: 0.71 - ETA: 11s - loss: 0.6434 - acc: 0.71 - ETA: 11s - loss: 0.6445 - acc: 0.71 - ETA

In [9]:
## Test the model: Report test accuracy, test sensitivity and test specificity
nasnet_predictions = [np.argmax(nasnet_model.predict(np.expand_dims(feature, axis=0))) for feature in test_features_nasnet]

test_accuracy = 100*np.sum(np.array(nasnet_predictions)==np.argmax(y_test, axis=1))/len(nasnet_predictions)
print('Test accuracy: %.4f%%' % test_accuracy)

nasnet_TP, nasnet_FP, nasnet_TN, nasnet_FN = perf_measure(y_test, nasnet_predictions)

nasnet_sensitivity = nasnet_TP / (nasnet_TP + nasnet_FN)
nasnet_specificity = nasnet_TN / (nasnet_TN + nasnet_FP)

print('Nasnet Test Sensitivity: %.4f%%' % nasnet_sensitivity)
print('Nasnet Test Specificity: %.4f%%' % nasnet_specificity)

Test accuracy: 75.4354%
Nasnet Test Sensitivity: 0.8052%
Nasnet Test Specificity: 0.7036%


### Robustness - Gaussian Noise (Nasnet)

In [3]:
from keras.applications.nasnet import NASNetMobile, preprocess_input
from keras.callbacks import TensorBoard
from time import time
from keras.layers import Conv2D, MaxPooling2D, GlobalAveragePooling2D
from keras.layers import Dropout, Flatten, Dense
from keras.models import Sequential
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping
from keras.layers import GaussianNoise

## Loading the NASNetLarge model with pre-trained ImageNet weights
model = NASNetMobile(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

## Preprocessing the data, so that it can be fed to the pre-trained NASNetLarge model. 
#nasnet_train_input = preprocess_input(train_tensors)
#nasnet_valid_input = preprocess_input(valid_tensors)
#nasnet_test_input = preprocess_input(test_tensors)

## Creating bottleneck features for the training data
#train_features_nasnet = model.predict(nasnet_train_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_train', features=train_features_nasnet)

## Creating bottleneck features for the testing data
#valid_features_nasnet = model.predict(nasnet_valid_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_valid', features=valid_features_nasnet)

## Creating bottleneck features for the testing data
#test_features_nasnet = model.predict(nasnet_test_input)
#np.savez('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_test', features=test_features_nasnet)

## Load bottleneck features for training data
train_features_nasnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_train.npz')
train_features_nasnet = train_features_nasnet['features']

## Load bottleneck features for validation data
valid_features_nasnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_valid.npz')
valid_features_nasnet = valid_features_nasnet['features']

## Load bottleneck features for testing data
test_features_nasnet = np.load('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/bottleneck_features/nasnet_features_test.npz')
test_features_nasnet = test_features_nasnet['features']


nasnet_model = Sequential()
nasnet_model.add(GaussianNoise(0.05, input_shape=train_features_nasnet.shape[1:]))
nasnet_model.add(Flatten())
nasnet_model.add(Dense(2, activation='softmax'))

nasnet_model.summary()

Instructions for updating:
Colocations handled automatically by placer.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
gaussian_noise_1 (GaussianNo (None, 7, 7, 1056)        0         
_________________________________________________________________
flatten_1 (Flatten)          (None, 51744)             0         
_________________________________________________________________
dense_1 (Dense)              (None, 2)                 103490    
Total params: 103,490
Trainable params: 103,490
Non-trainable params: 0
_________________________________________________________________


In [4]:
checkpointer_nasnet = ModelCheckpoint(filepath='C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.nasnet_robustness.hdf5', 
                               verbose=1, save_best_only=True)

nasnet_model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

nasnet_model.fit(train_features_nasnet, y_train, 
          validation_data=(valid_features_nasnet, y_val),
          epochs=20, batch_size=20, callbacks=[checkpointer_nasnet], verbose=1)

nasnet_model.load_weights('C:\\Users/user/OneDrive/Documents/capstone/Project_Main/saved_models/weights.best.nasnet_robustness.hdf5')


Instructions for updating:
Use tf.cast instead.
Train on 16534 samples, validate on 5512 samples
Epoch 1/20


 7880/16534 [=============>................] - ETA: 2:10:54 - loss: 0.6990 - acc: 0.50 - ETA: 43:57 - loss: 3.6010 - acc: 0.4667 - ETA: 33:08 - loss: 4.0047 - acc: 0.46 - ETA: 26:39 - loss: 4.5019 - acc: 0.47 - ETA: 22:19 - loss: 4.9662 - acc: 0.45 - ETA: 19:14 - loss: 4.7666 - acc: 0.43 - ETA: 15:04 - loss: 4.3484 - acc: 0.44 - ETA: 13:37 - loss: 4.1210 - acc: 0.47 - ETA: 11:26 - loss: 4.0471 - acc: 0.46 - ETA: 9:52 - loss: 3.7234 - acc: 0.4750 - ETA: 8:41 - loss: 3.6598 - acc: 0.471 - ETA: 7:45 - loss: 3.4262 - acc: 0.461 - ETA: 7:02 - loss: 3.3917 - acc: 0.462 - ETA: 6:26 - loss: 3.2238 - acc: 0.459 - ETA: 5:56 - loss: 3.1720 - acc: 0.456 - ETA: 5:30 - loss: 3.0600 - acc: 0.467 - ETA: 5:20 - loss: 2.9731 - acc: 0.468 - ETA: 4:59 - loss: 2.8736 - acc: 0.469 - ETA: 4:51 - loss: 2.8230 - acc: 0.465 - ETA: 4:34 - loss: 2.7201 - acc: 0.467 - ETA: 4:19 - loss: 2.6334 - acc: 0.473 - ETA: 4:13 - loss: 2.5793 - acc: 0.474 - ETA: 4:01 - loss: 2.4981 - acc: 0.471 - ETA: 3:50 - loss: 2.4068 - a

15340/16534 [==========================>...] - ETA: 29s - loss: 1.0341 - acc: 0.53 - ETA: 29s - loss: 1.0337 - acc: 0.53 - ETA: 28s - loss: 1.0334 - acc: 0.53 - ETA: 28s - loss: 1.0321 - acc: 0.53 - ETA: 28s - loss: 1.0313 - acc: 0.53 - ETA: 28s - loss: 1.0300 - acc: 0.54 - ETA: 28s - loss: 1.0288 - acc: 0.54 - ETA: 28s - loss: 1.0278 - acc: 0.54 - ETA: 27s - loss: 1.0258 - acc: 0.54 - ETA: 27s - loss: 1.0242 - acc: 0.54 - ETA: 27s - loss: 1.0227 - acc: 0.54 - ETA: 27s - loss: 1.0208 - acc: 0.54 - ETA: 27s - loss: 1.0204 - acc: 0.54 - ETA: 26s - loss: 1.0198 - acc: 0.54 - ETA: 26s - loss: 1.0194 - acc: 0.54 - ETA: 26s - loss: 1.0189 - acc: 0.54 - ETA: 26s - loss: 1.0172 - acc: 0.54 - ETA: 26s - loss: 1.0157 - acc: 0.54 - ETA: 26s - loss: 1.0139 - acc: 0.54 - ETA: 25s - loss: 1.0131 - acc: 0.54 - ETA: 25s - loss: 1.0116 - acc: 0.54 - ETA: 25s - loss: 1.0097 - acc: 0.54 - ETA: 25s - loss: 1.0081 - acc: 0.54 - ETA: 25s - loss: 1.0066 - acc: 0.54 - ETA: 25s - loss: 1.0046 - acc: 0.54 - ETA

16534/16534 [==============================] - ETA: 3s - loss: 0.9625 - acc: 0.559 - ETA: 3s - loss: 0.9621 - acc: 0.559 - ETA: 3s - loss: 0.9614 - acc: 0.559 - ETA: 3s - loss: 0.9613 - acc: 0.559 - ETA: 3s - loss: 0.9611 - acc: 0.559 - ETA: 2s - loss: 0.9616 - acc: 0.559 - ETA: 2s - loss: 0.9612 - acc: 0.559 - ETA: 2s - loss: 0.9611 - acc: 0.559 - ETA: 2s - loss: 0.9610 - acc: 0.559 - ETA: 2s - loss: 0.9602 - acc: 0.559 - ETA: 2s - loss: 0.9597 - acc: 0.560 - ETA: 2s - loss: 0.9588 - acc: 0.560 - ETA: 2s - loss: 0.9587 - acc: 0.560 - ETA: 2s - loss: 0.9584 - acc: 0.560 - ETA: 2s - loss: 0.9580 - acc: 0.560 - ETA: 2s - loss: 0.9576 - acc: 0.560 - ETA: 2s - loss: 0.9566 - acc: 0.561 - ETA: 1s - loss: 0.9562 - acc: 0.561 - ETA: 1s - loss: 0.9556 - acc: 0.561 - ETA: 1s - loss: 0.9557 - acc: 0.562 - ETA: 1s - loss: 0.9554 - acc: 0.562 - ETA: 1s - loss: 0.9567 - acc: 0.562 - ETA: 1s - loss: 0.9565 - acc: 0.562 - ETA: 1s - loss: 0.9571 - acc: 0.562 - ETA: 1s - loss: 0.9570 - acc: 0.562 - ETA

 4800/16534 [=======>......................] - ETA: 1:17 - loss: 1.8215 - acc: 0.450 - ETA: 1:17 - loss: 1.5109 - acc: 0.400 - ETA: 1:12 - loss: 1.1999 - acc: 0.500 - ETA: 1:10 - loss: 1.3937 - acc: 0.512 - ETA: 1:11 - loss: 1.4850 - acc: 0.490 - ETA: 1:10 - loss: 1.3511 - acc: 0.500 - ETA: 1:09 - loss: 1.3632 - acc: 0.500 - ETA: 1:10 - loss: 1.4085 - acc: 0.487 - ETA: 1:09 - loss: 1.3418 - acc: 0.488 - ETA: 1:08 - loss: 1.4136 - acc: 0.480 - ETA: 1:09 - loss: 1.4353 - acc: 0.481 - ETA: 1:08 - loss: 1.3682 - acc: 0.495 - ETA: 1:08 - loss: 1.3169 - acc: 0.503 - ETA: 1:08 - loss: 1.3092 - acc: 0.503 - ETA: 1:09 - loss: 1.3015 - acc: 0.503 - ETA: 1:08 - loss: 1.2745 - acc: 0.496 - ETA: 1:08 - loss: 1.2692 - acc: 0.500 - ETA: 1:08 - loss: 1.2755 - acc: 0.497 - ETA: 1:08 - loss: 1.2452 - acc: 0.505 - ETA: 1:08 - loss: 1.2167 - acc: 0.512 - ETA: 1:08 - loss: 1.2091 - acc: 0.509 - ETA: 1:07 - loss: 1.1933 - acc: 0.518 - ETA: 1:08 - loss: 1.1724 - acc: 0.519 - ETA: 1:07 - loss: 1.1689 - acc: 0

...

12880/16534 [======================>.......] - ETA: 39s - loss: 0.9854 - acc: 0.65 - ETA: 39s - loss: 0.9862 - acc: 0.65 - ETA: 39s - loss: 0.9839 - acc: 0.65 - ETA: 39s - loss: 0.9841 - acc: 0.65 - ETA: 39s - loss: 0.9826 - acc: 0.65 - ETA: 38s - loss: 0.9822 - acc: 0.65 - ETA: 38s - loss: 0.9825 - acc: 0.65 - ETA: 38s - loss: 0.9808 - acc: 0.65 - ETA: 38s - loss: 0.9792 - acc: 0.65 - ETA: 37s - loss: 0.9768 - acc: 0.65 - ETA: 37s - loss: 0.9748 - acc: 0.65 - ETA: 37s - loss: 0.9749 - acc: 0.65 - ETA: 37s - loss: 0.9743 - acc: 0.65 - ETA: 36s - loss: 0.9739 - acc: 0.65 - ETA: 36s - loss: 0.9742 - acc: 0.65 - ETA: 36s - loss: 0.9750 - acc: 0.65 - ETA: 36s - loss: 0.9776 - acc: 0.65 - ETA: 36s - loss: 0.9809 - acc: 0.65 - ETA: 35s - loss: 0.9791 - acc: 0.65 - ETA: 35s - loss: 0.9763 - acc: 0.65 - ETA: 35s - loss: 0.9746 - acc: 0.65 - ETA: 35s - loss: 0.9723 - acc: 0.65 - ETA: 35s - loss: 0.9713 - acc: 0.65 - ETA: 35s - loss: 0.9685 - acc: 0.65 - ETA: 34s - loss: 0.9706 - acc: 0.65 - ETA

16534/16534 [==============================] - ETA: 9s - loss: 0.9961 - acc: 0.648 - ETA: 9s - loss: 0.9953 - acc: 0.648 - ETA: 9s - loss: 0.9952 - acc: 0.648 - ETA: 9s - loss: 0.9939 - acc: 0.648 - ETA: 9s - loss: 0.9937 - acc: 0.648 - ETA: 9s - loss: 0.9927 - acc: 0.649 - ETA: 8s - loss: 0.9927 - acc: 0.649 - ETA: 8s - loss: 0.9909 - acc: 0.649 - ETA: 8s - loss: 0.9903 - acc: 0.649 - ETA: 8s - loss: 0.9903 - acc: 0.649 - ETA: 8s - loss: 0.9883 - acc: 0.650 - ETA: 8s - loss: 0.9876 - acc: 0.650 - ETA: 8s - loss: 0.9880 - acc: 0.650 - ETA: 8s - loss: 0.9876 - acc: 0.650 - ETA: 8s - loss: 0.9871 - acc: 0.650 - ETA: 7s - loss: 0.9855 - acc: 0.650 - ETA: 7s - loss: 0.9847 - acc: 0.650 - ETA: 7s - loss: 0.9838 - acc: 0.651 - ETA: 7s - loss: 0.9843 - acc: 0.650 - ETA: 7s - loss: 0.9841 - acc: 0.651 - ETA: 7s - loss: 0.9848 - acc: 0.651 - ETA: 7s - loss: 0.9840 - acc: 0.651 - ETA: 7s - loss: 0.9850 - acc: 0.650 - ETA: 7s - loss: 0.9865 - acc: 0.650 - ETA: 6s - loss: 0.9873 - acc: 0.650 - ETA

 4260/16534 [======>.......................] - ETA: 51s - loss: 0.9738 - acc: 0.50 - ETA: 57s - loss: 0.8003 - acc: 0.60 - ETA: 1:00 - loss: 0.7586 - acc: 0.583 - ETA: 1:01 - loss: 0.7734 - acc: 0.650 - ETA: 59s - loss: 0.7949 - acc: 0.650 - ETA: 59s - loss: 0.7885 - acc: 0.65 - ETA: 1:00 - loss: 0.7841 - acc: 0.650 - ETA: 1:00 - loss: 0.7925 - acc: 0.643 - ETA: 1:01 - loss: 0.7700 - acc: 0.650 - ETA: 1:01 - loss: 0.8347 - acc: 0.615 - ETA: 1:01 - loss: 0.8064 - acc: 0.622 - ETA: 1:01 - loss: 0.8293 - acc: 0.633 - ETA: 1:02 - loss: 0.8486 - acc: 0.623 - ETA: 1:02 - loss: 0.8121 - acc: 0.639 - ETA: 1:01 - loss: 0.7820 - acc: 0.650 - ETA: 1:02 - loss: 0.7754 - acc: 0.659 - ETA: 1:02 - loss: 0.7838 - acc: 0.652 - ETA: 1:02 - loss: 0.8042 - acc: 0.652 - ETA: 1:02 - loss: 0.8266 - acc: 0.647 - ETA: 1:02 - loss: 0.8377 - acc: 0.642 - ETA: 1:02 - loss: 0.8347 - acc: 0.645 - ETA: 1:02 - loss: 0.8443 - acc: 0.643 - ETA: 1:01 - loss: 0.8168 - acc: 0.654 - ETA: 1:01 - loss: 0.8350 - acc: 0.647 - 

10120/16534 [=================>............] - ETA: 45s - loss: 1.0594 - acc: 0.63 - ETA: 45s - loss: 1.0589 - acc: 0.63 - ETA: 45s - loss: 1.0585 - acc: 0.63 - ETA: 45s - loss: 1.0588 - acc: 0.63 - ETA: 45s - loss: 1.0629 - acc: 0.63 - ETA: 45s - loss: 1.0611 - acc: 0.63 - ETA: 44s - loss: 1.0595 - acc: 0.63 - ETA: 44s - loss: 1.0610 - acc: 0.63 - ETA: 44s - loss: 1.0619 - acc: 0.63 - ETA: 44s - loss: 1.0603 - acc: 0.63 - ETA: 44s - loss: 1.0602 - acc: 0.63 - ETA: 44s - loss: 1.0589 - acc: 0.63 - ETA: 44s - loss: 1.0576 - acc: 0.63 - ETA: 44s - loss: 1.0571 - acc: 0.63 - ETA: 44s - loss: 1.0553 - acc: 0.63 - ETA: 44s - loss: 1.0559 - acc: 0.63 - ETA: 44s - loss: 1.0554 - acc: 0.63 - ETA: 44s - loss: 1.0567 - acc: 0.63 - ETA: 44s - loss: 1.0578 - acc: 0.63 - ETA: 43s - loss: 1.0590 - acc: 0.63 - ETA: 43s - loss: 1.0592 - acc: 0.63 - ETA: 43s - loss: 1.0583 - acc: 0.63 - ETA: 43s - loss: 1.0632 - acc: 0.63 - ETA: 43s - loss: 1.0636 - acc: 0.63 - ETA: 43s - loss: 1.0630 - acc: 0.63 - ETA

16534/16534 [==============================] - ETA: 20s - loss: 0.9884 - acc: 0.64 - ETA: 19s - loss: 0.9884 - acc: 0.64 - ETA: 19s - loss: 0.9886 - acc: 0.64 - ETA: 19s - loss: 0.9874 - acc: 0.64 - ETA: 19s - loss: 0.9860 - acc: 0.64 - ETA: 19s - loss: 0.9860 - acc: 0.64 - ETA: 19s - loss: 0.9846 - acc: 0.64 - ETA: 19s - loss: 0.9833 - acc: 0.64 - ETA: 18s - loss: 0.9816 - acc: 0.64 - ETA: 18s - loss: 0.9805 - acc: 0.64 - ETA: 18s - loss: 0.9818 - acc: 0.64 - ETA: 18s - loss: 0.9836 - acc: 0.64 - ETA: 18s - loss: 0.9838 - acc: 0.64 - ETA: 18s - loss: 0.9899 - acc: 0.64 - ETA: 18s - loss: 0.9908 - acc: 0.64 - ETA: 17s - loss: 0.9982 - acc: 0.64 - ETA: 17s - loss: 0.9997 - acc: 0.64 - ETA: 17s - loss: 1.0093 - acc: 0.64 - ETA: 17s - loss: 1.0099 - acc: 0.64 - ETA: 17s - loss: 1.0150 - acc: 0.64 - ETA: 17s - loss: 1.0173 - acc: 0.64 - ETA: 16s - loss: 1.0213 - acc: 0.64 - ETA: 16s - loss: 1.0219 - acc: 0.64 - ETA: 16s - loss: 1.0219 - acc: 0.64 - ETA: 16s - loss: 1.0207 - acc: 0.64 - ETA

In [6]:
## Test the model: Report test accuracy, test sensitivity and test specificity
nasnet_predictions = [np.argmax(nasnet_model.predict(np.expand_dims(feature, axis=0))) for feature in test_features_nasnet]

test_accuracy = 100*np.sum(np.array(nasnet_predictions)==np.argmax(y_test, axis=1))/len(nasnet_predictions)
print('Test accuracy: %.4f%%' % test_accuracy)

nasnet_TP, nasnet_FP, nasnet_TN, nasnet_FN = perf_measure(y_test, nasnet_predictions)

nasnet_sensitivity = nasnet_TP / (nasnet_TP + nasnet_FN)
nasnet_specificity = nasnet_TN / (nasnet_TN + nasnet_FP)

print('Nasnet Test Sensitivity: %.4f%%' % nasnet_sensitivity)
print('Nasnet Test Specificity: %.4f%%' % nasnet_specificity)
print(nasnet_TP, nasnet_TN, nasnet_FP, nasnet_FN)

Test accuracy: 74.0929%
Nasnet Test Sensitivity: 0.8147%
Nasnet Test Specificity: 0.6674%
2242 1842 918 510
